## 原始数据分析

查看数据长度分布

In [4]:
import pandas as pd
len_list = []
file_list = ['test', 'train', 'val']
for file in file_list:
    with open(f'../data/fold0/{file}/sentences.txt', 'r', encoding='utf-8') as f:
        len_list += [len(line.strip().split(' ')) for line in f]
print(pd.Series(len_list).describe(percentiles=[.25, .5, .75, .85, .95]))

count    500.000000
mean     150.672000
std       44.065815
min       36.000000
25%      119.750000
50%      147.500000
75%      176.250000
85%      191.150000
95%      224.000000
max      358.000000
dtype: float64


查看分类别实体长度

In [15]:
import sys
sys.path.insert(0, '../')

In [16]:
from metrics import get_entities
from utils import IO2STR

In [17]:
# data_dir = ['../data/fold0/val/', '../data/fold0/train/']
data_dir = ['../data/fold0/test/']

In [18]:
sentences = []
tags = []
for dir_ in data_dir:
    with open(dir_+'sentences.txt', 'r', encoding='utf-8') as f_sen,\
        open(dir_+'tags.txt', 'r', encoding='utf-8') as f_tag:
        sentences.extend([line.strip().split(' ') for line in f_sen])
        tags.extend([line.strip().split(' ') for line in f_tag])

In [83]:
y_true = []
for s,t in zip(sentences, tags):
    entities = get_entities(t)
    sample = []
    for entity in entities:
        entity_con = s[entity[1]:entity[2]+1]
        entity_type = IO2STR[entity[0]]
        sample.append((entity_type, ''.join(entity_con)))
    y_true.extend(sample) 

In [84]:
y_true

[('试验要素', '“全球定位系统下一代操作控制系统”(GPS?OCX)'),
 ('试验要素', '合格试验'),
 ('试验要素', '发射和校验系统'),
 ('任务场景', '美军方'),
 ('任务场景', '平民'),
 ('任务场景', 'GPS'),
 ('性能指标', '可用性'),
 ('性能指标', '精度'),
 ('性能指标', '安全性'),
 ('试验要素', 'GPSⅢ卫星'),
 ('性能指标', '发射和早期轨道校验功能'),
 ('性能指标', '网络安全'),
 ('性能指标', '功能'),
 ('试验要素', '“鲉鱼”级潜艇首艇“'),
 ('试验要素', '卡尔瓦里”号'),
 ('系统组成', '柴电'),
 ('系统组成', '不依赖空气推进系统'),
 ('试验要素', '新型海基“铁穹”系统拦截试验'),
 ('性能指标', '海上战略资产'),
 ('试验要素', '“萨尔”-5型“艾拉特”级护卫舰'),
 ('试验要素', '海基“铁穹”系统'),
 ('试验要素', '岸基发射'),
 ('试验要素', '近程火箭弹靶弹'),
 ('试验要素', '“高超声速国际飞行研究试验”(HIFiRE)'),
 ('试验要素', '飞行试验'),
 ('试验要素', '试验性火箭'),
 ('性能指标', '高度'),
 ('性能指标', '目标速度'),
 ('试验要素', '“约翰·保罗·琼斯”号'),
 ('试验要素', '驱逐舰'),
 ('试验要素', '“宙斯盾”导弹防御系统'),
 ('试验要素', '飞行试验'),
 ('试验要素', '中程弹道导弹目标'),
 ('系统组成', 'AN/SPY-1雷达'),
 ('试验要素', '“可重复使用运载器—技术验证机”(RLV-TD)'),
 ('试验要素', 'HS9固体运载火箭'),
 ('试验要素', '指定海域'),
 ('试验要素', '飞行过程'),
 ('试验要素', '地面站'),
 ('试验要素', '测量船'),
 ('试验要素', '智能反机场武器'),
 ('试验要素', '“美洲虎”飞机'),
 ('性能指标', '重'),
 ('性能指标', '打击距离'),
 ('试验要素', '“网络集成鉴定”(NIE)16.2'),


In [85]:
import pandas as pd

In [12]:
df = pd.DataFrame({
    "type": [ne[0] for ne in y_true],
    "content": [ne[1] for ne in y_true]
})

In [13]:
df['length'] = df.apply(lambda row: len(row.content), axis=1)

In [14]:
df

type      content  length
0     试验要素   “加尔各答”级驱逐舰      10
1     试验要素       远程面空导弹       6
2     试验要素      增程型空中目标       7
3     试验要素    “巴拉克”-8导弹       9
4     试验要素  波音KC-46A加油机      11
...    ...          ...     ...
3156  试验要素   高空“伪卫星”无人机      10
3157  性能指标         有效载荷       4
3158  系统组成        通信中继器       5
3159  系统组成       拍照录像设备       6
3160  系统组成         气象设备       4

[3161 rows x 3 columns]

In [15]:
# 按类别分组
df_gb = df.groupby('type')

分类别实体个数

In [87]:
from collections import Counter

In [88]:
with open('./val_freq.txt', 'w', encoding='utf-8') as f:
    for entity, freq in Counter(y_true).most_common():
        f.write(f'{entity[0]}\t{entity[1]}\t{freq}\n')

In [115]:
for c in df.loc[df_gb.groups['试验要素']]['content'].tolist():
    if "方案" in c:
        print(c)

方案
拦截方案
火控拦截方案
解决方案
设计方案
飞行器方案


In [80]:
df_gb.count()

content  length
type                 
任务场景      516     516
性能指标      712     712
系统组成      396     396
试验要素     1537    1537

分类别实体长度

In [2]:
from collections import Counter

In [94]:
df_gb["length"].mean()

type
任务场景    5.106589
性能指标    3.817416
系统组成    5.207071
试验要素    8.554327
Name: length, dtype: float64

In [101]:
sorted(Counter(df.loc[df_gb.groups['任务场景']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(1, 1),
 (2, 103),
 (3, 52),
 (4, 158),
 (5, 35),
 (6, 54),
 (7, 27),
 (8, 21),
 (9, 14),
 (10, 12),
 (11, 11),
 (12, 10),
 (13, 5),
 (14, 3),
 (15, 3),
 (16, 2),
 (17, 1),
 (18, 2),
 (19, 1),
 (41, 1)]

In [102]:
sorted(Counter(df.loc[df_gb.groups['性能指标']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(1, 27),
 (2, 208),
 (3, 99),
 (4, 222),
 (5, 34),
 (6, 56),
 (7, 26),
 (8, 11),
 (9, 9),
 (10, 10),
 (11, 3),
 (12, 2),
 (13, 3),
 (14, 1),
 (23, 1)]

In [103]:
sorted(Counter(df.loc[df_gb.groups['系统组成']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(1, 1),
 (2, 65),
 (3, 60),
 (4, 82),
 (5, 42),
 (6, 43),
 (7, 33),
 (8, 22),
 (9, 10),
 (10, 14),
 (11, 7),
 (12, 6),
 (13, 1),
 (14, 2),
 (15, 3),
 (16, 3),
 (17, 1),
 (18, 1)]

In [129]:
df.loc[df_gb.groups['系统组成']][df.length==1]

D:\Software\Anaconda\lib\site-packages\ipykernel_launcher.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  """Entry point for launching an IPython kernel.


type content  length
2207  系统组成       翼       1

In [105]:
sorted(Counter(df.loc[df_gb.groups['试验要素']]['length'].tolist()).most_common(), key=lambda x: x[0])

[(1, 3),
 (2, 100),
 (3, 60),
 (4, 282),
 (5, 76),
 (6, 189),
 (7, 95),
 (8, 129),
 (9, 87),
 (10, 77),
 (11, 58),
 (12, 59),
 (13, 65),
 (14, 45),
 (15, 39),
 (16, 28),
 (17, 28),
 (18, 25),
 (19, 19),
 (20, 18),
 (21, 9),
 (22, 9),
 (23, 10),
 (24, 5),
 (25, 5),
 (26, 4),
 (27, 3),
 (28, 2),
 (29, 2),
 (30, 1),
 (33, 1),
 (35, 1),
 (36, 2),
 (41, 1)]

## Badcase分析

In [56]:
from pathlib import Path

In [57]:
import sys
sys.path.insert(0, '../')

In [58]:
from metrics import get_entities
from utils import IO2STR

In [384]:
val_data_dir = Path('../data/fold0/val/')

In [385]:
with open(val_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen,\
    open(val_data_dir/'tags.txt', 'r', encoding='utf-8') as f_tag:
    sentences = [line.strip().split(' ') for line in f_sen]
    tags = [line.strip().split(' ') for line in f_tag]

获取gold label

In [386]:
y_true = []
for s,t in zip(sentences, tags):
    entities = get_entities(t)
    sample = []
    for entity in entities:
        entity_con = s[entity[1]:entity[2]+1]
        entity_type = IO2STR[entity[0]]
        sample.append((entity_type, ''.join(entity_con), entity[1], entity[2]+1))
    y_true.append(sample) 

In [387]:
y_true

[[('试验要素', '“加尔各答”级驱逐舰', 7, 17),
  ('试验要素', '远程面空导弹', 33, 39),
  ('试验要素', '增程型空中目标', 79, 86),
  ('试验要素', '“巴拉克”-8导弹', 92, 101)],
 [('试验要素', '波音KC-46A加油机', 16, 27),
  ('试验要素', '空中加油试验', 40, 46),
  ('性能指标', '飞行高度', 113, 117),
  ('试验要素', 'F-16战斗机', 122, 129),
  ('试验要素', '燃油', 137, 139),
  ('系统组成', '吊杆', 150, 152),
  ('系统组成', '伸缩管', 153, 156),
  ('系统组成', '插孔', 165, 167),
  ('试验要素', '受油机', 168, 171)],
 [('试验要素', '无人潜航器', 50, 55),
  ('试验要素', '通用控制系统', 63, 69),
  ('试验要素', '软件架构', 76, 80),
  ('系统组成', '框架', 86, 88),
  ('系统组成', '用户界面', 89, 93),
  ('系统组成', '元件', 94, 96),
  ('任务场景', '无人系统', 104, 108),
  ('任务场景', '海军无人系统', 112, 118),
  ('任务场景', '航行器管理', 123, 128),
  ('任务场景', '任务计划', 129, 133),
  ('任务场景', '任务管理能力', 134, 140)],
 [('系统组成', '第一级', 23, 26),
  ('系统组成', '主发动机', 29, 33),
  ('试验要素', '“南半球运载火箭”项目', 40, 51),
  ('试验要素', '方案', 65, 67),
  ('试验要素', '飞行试验', 69, 73),
  ('系统组成', '带翼助推器', 85, 90),
  ('系统组成', '超燃冲压发动机', 92, 99),
  ('系统组成', '第二级', 107, 110)],
 [('试验要素', '“地基中段防御系统”', 49, 59),
  ('试验要素'

In [388]:
for sen, pre, true in zip(sentences, y_pre, y_true):
#     if "".join(sen) != 'N':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print(sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
#         print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
#         print(sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
#         print('-*-'*40)
        print('true_label:', sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
#         print('pre_label:', sorted(pre, key=lambda p: p[2]))
        print('\n')

印度海军近日从“加尔各答”级驱逐舰上试射了由印度和以色列联合研制的远程面空导弹?试验在位于印度西海岸的“加尔各答”级驱逐舰上进行?试验中,该导弹成功拦截了一个增程型空中目标?此次试验的“巴拉克”-8导弹由印度国防研究与发展局?以色列航空工业公司?以色列武器研发与技术基础设施管理局?埃尔塔系统公司?拉法尔公司等机构联合研制?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
true_label: [('试验要素', '“加尔各答”级驱逐舰', 7, 17), ('试验要素', '远程面空导弹', 33, 39), ('试验要素', '增程型空中目标', 79, 86), ('试验要素', '“巴拉克”-8导弹', 92, 101)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-


美国空军24日在华盛顿州成功完成波音KC-46A加油机(工程与制造第2阶段)首次空中加油试验,开启了空中加油演示验证的里程碑C阶段?作为开发的一部分,试验小组完成了一系列试验,然后在波音机场为时5小时45分钟的出行架次中向1架飞行高度为6千米的F-16战斗机输送了726千克燃油?此外,加油机还部署了吊杆,伸缩管向外探出,伸向配备插孔的受油机?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
true_label: [('试验要素', '波音KC-46A加油机', 16, 27), ('试验要素', '空中加油试验', 40, 46), ('性能指标', '飞行高度', 113, 117), ('试验要素', 'F-16战斗机', 122, 129), ('试验要素', '燃油', 137, 139), ('系统组成'

获取pre label

version_1

In [244]:
ex1_dir = Path('../experiments/train/fusion_submit.json')

In [245]:
import json

In [246]:
with open(ex1_dir, 'r', encoding='utf-8') as f:
    pre = json.load(f)

In [278]:
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos']-1, entity['end_pos']))
    y_pre.append(sample)

IndexError: list index out of range

In [248]:
y_pre

[[('试验要素', '“全球定位系统下一代操作控制系统”(GPS?OCX)', 18, 44),
  ('试验要素', '合格试验', 47, 51),
  ('试验要素', '发射和校验系统', 53, 60),
  ('任务场景', '美军方', 75, 78),
  ('任务场景', '平民', 79, 81),
  ('任务场景', 'GPS', 85, 88),
  ('性能指标', '可用性', 93, 96),
  ('性能指标', '精度', 97, 99),
  ('性能指标', '安全性', 100, 103),
  ('试验要素', 'GPSⅢ卫星', 111, 117),
  ('性能指标', '发射和早期轨道校验功能', 119, 130),
  ('性能指标', '网络安全', 146, 150),
  ('性能指标', '功能', 150, 152)],
 [('试验要素', '“鲉鱼”级潜艇首艇“', 17, 27),
  ('试验要素', '卡尔瓦里”号', 27, 33),
  ('系统组成', '柴电', 95, 97),
  ('系统组成', '不依赖空气推进系统', 106, 115)],
 [('试验要素', '新型海基“铁穹”系统拦截试验', 8, 22),
  ('性能指标', '海上战略资产', 32, 38),
  ('试验要素', '“萨尔”-5型“艾拉特”级护卫舰', 56, 72),
  ('试验要素', '海基“铁穹”系统', 74, 82),
  ('试验要素', '岸基发射', 88, 92),
  ('试验要素', '近程火箭弹靶弹', 93, 100)],
 [('试验要素', '“高超声速国际飞行研究试验”(HIFiRE)', 11, 33),
  ('试验要素', '飞行试验', 43, 47),
  ('试验要素', '试验性火箭', 48, 53),
  ('性能指标', '高度', 63, 65),
  ('性能指标', '目标速度', 75, 79)],
 [('试验要素', '“约翰·保罗·琼斯”号', 15, 26),
  ('试验要素', '驱逐舰', 26, 29),
  ('试验要素', '“宙斯盾”导弹防御系统', 33, 44),
  ('试验要素', '飞行试验', 4

In [249]:
for sen, pre, true in zip(sentences, y_pre, y_true):
#     if "".join(sen) != 'N':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print(sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
#         print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
#         print(sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
#         print('-*-'*40)
        print('true_label:', sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('pre_label:', sorted(pre, key=lambda p: p[2]))
        print('\n')

3月4日,雷声公司成功通过了美国空军“全球定位系统下一代操作控制系统”(GPS?OCX)第一次合格试验,是发射和校验系统的一个里程碑?该系统可显著改进美军方和平民所依赖的GPS,包括增强可用性?精度和安全性,还可为现代化的GPSⅢ卫星提供发射和早期轨道校验功能,并为整个OCX项目提供77%的网络安全功能?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
true_label: [('试验要素', '“全球定位系统下一代操作控制系统”(GPS?OCX)', 18, 44), ('试验要素', '合格试验', 47, 51), ('试验要素', '发射和校验系统', 53, 60), ('任务场景', '美军方', 75, 78), ('任务场景', '平民', 79, 81), ('任务场景', 'GPS', 85, 88), ('性能指标', '可用性', 93, 96), ('性能指标', '精度', 97, 99), ('性能指标', '安全性', 100, 103), ('试验要素', 'GPSⅢ卫星', 111, 117), ('性能指标', '发射和早期轨道校验功能', 119, 130), ('性能指标', '网络安全', 146, 150), ('性能指标', '功能', 150, 152)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
pre_label: [('试验要素', '“全球定位系统下一代操作控制系统”(GPS?OCX)', 18, 44), ('试验要素', '合格试验', 47, 51), ('试验要素', '发射和校验系统', 53, 60), ('任务场景', '美军方', 75, 78), ('任务场景', '平民', 79, 81), ('任务场景', 'GPS', 85, 88), ('性能指标', '可用性', 93, 96), ('性能指

In [99]:
ex2_dir = Path('./val_result/boundary_vocab.json')

In [100]:
with open(ex2_dir, 'r', encoding='utf-8') as f:
    pre = json.load(f)

In [101]:
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'validate_V2_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos']-1, entity['end_pos']))
    y_pre.append(sample)

In [102]:
y_pre

[[('试验要素', '“加尔各答”级驱逐舰', 7, 17),
  ('试验要素', '远程面空导弹', 33, 39),
  ('试验要素', '增程型空中目标', 79, 86)],
 [('试验要素', '波音KC-46A加油机(工程与制造第2阶段)', 16, 38),
  ('试验要素', '空中加油试验', 40, 46),
  ('试验要素', '空中加油演示验证', 50, 58),
  ('试验要素', '出行架次', 105, 109),
  ('性能指标', '飞行高度', 113, 117),
  ('试验要素', 'F-16战斗机', 122, 129),
  ('试验要素', '燃油', 137, 139),
  ('系统组成', '吊杆', 150, 152),
  ('系统组成', '伸缩管', 153, 156),
  ('系统组成', '插孔', 165, 167),
  ('试验要素', '受油机', 168, 171)],
 [('试验要素', '无人潜航器', 50, 55),
  ('试验要素', '通用控制系统', 63, 69),
  ('试验要素', '软件架构', 76, 80),
  ('系统组成', '软件架构', 76, 80),
  ('系统组成', '框架', 86, 88),
  ('系统组成', '用户界面', 89, 93),
  ('系统组成', '元件', 94, 96),
  ('试验要素', '无人系统', 104, 108),
  ('试验要素', '海军无人系统', 112, 118),
  ('性能指标', '航行器管理', 123, 128),
  ('性能指标', '任务计划', 129, 133),
  ('性能指标', '任务管理能力', 134, 140)],
 [('试验要素', '可重复使用运载火箭项目', 2, 13),
  ('性能指标', '垂直降落', 18, 22),
  ('系统组成', '第一级', 23, 26),
  ('系统组成', '回收主发动机', 27, 33),
  ('试验要素', '“南半球运载火箭”项目', 40, 51),
  ('任务场景', '发射成本', 58, 62),
  ('试验要素', '不同方案', 63, 67),


In [218]:
for sen, pre, true in zip(sentences, y_pre, y_true):
    if "".join(sen) != 'N':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print(sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
#         print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
#         print(sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
#         print('-*-'*40)
        print(sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print(sorted(pre, key=lambda p: p[2]))
        print('\n')

3月4日,雷声公司成功通过了美国空军“全球定位系统下一代操作控制系统”(GPS?OCX)第一次合格试验,是发射和校验系统的一个里程碑?该系统可显著改进美军方和平民所依赖的GPS,包括增强可用性?精度和安全性,还可为现代化的GPSⅢ卫星提供发射和早期轨道校验功能,并为整个OCX项目提供77%的网络安全功能?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“全球定位系统下一代操作控制系统”(GPS?OCX)', 18, 44), ('试验要素', '合格试验', 47, 51), ('试验要素', '发射和校验系统', 53, 60), ('任务场景', '美军方', 75, 78), ('任务场景', '平民', 79, 81), ('任务场景', 'GPS', 85, 88), ('性能指标', '可用性', 93, 96), ('性能指标', '精度', 97, 99), ('性能指标', '安全性', 100, 103), ('试验要素', 'GPSⅢ卫星', 111, 117), ('性能指标', '发射和早期轨道校验功能', 119, 130), ('性能指标', '网络安全', 146, 150), ('性能指标', '功能', 150, 152)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '公司成功通过了美国空', 7, 17), ('试验要素', '“全球定位系统下一代操作控制系统”(GPS?OCX)', 18, 44), ('试验要素', '统”(GPS', 33, 39), ('试验要素', '合格试验', 47, 51), ('试验要素', '发射和校验系统', 53, 60), ('任务场景', '美军方', 75, 78), ('试验要素', '平民所依赖的G', 79, 86), ('试验要素', '强可用性

In [107]:
ex3_dir = Path('./val_result/better.json')

In [108]:
with open(ex3_dir, 'r', encoding='utf-8') as f:
    pre = json.load(f)

In [109]:
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'validate_V2_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos']-1, entity['end_pos']))
    y_pre.append(sample)

In [110]:
y_pre

[[('试验要素', '“加尔各答”级驱逐舰', 7, 17),
  ('试验要素', '远程面空导弹', 33, 39),
  ('试验要素', '增程型空中目标', 79, 86)],
 [('试验要素', '波音KC-46A加油机(工程与制造第2阶段)', 16, 38),
  ('试验要素', '空中加油试验', 40, 46),
  ('试验要素', '空中加油演示验证', 50, 58),
  ('试验要素', '出行架次', 105, 109),
  ('性能指标', '飞行高度', 113, 117),
  ('试验要素', 'F-16战斗机', 122, 129),
  ('试验要素', '燃油', 137, 139),
  ('系统组成', '吊杆', 150, 152),
  ('系统组成', '伸缩管', 153, 156),
  ('系统组成', '插孔', 165, 167),
  ('系统组成', '受油机', 168, 171)],
 [('试验要素', '无人潜航器', 50, 55),
  ('试验要素', '通用控制系统', 63, 69),
  ('系统组成', '软件架构', 76, 80),
  ('系统组成', '框架', 86, 88),
  ('系统组成', '用户界面', 89, 93),
  ('系统组成', '元件', 94, 96),
  ('试验要素', '无人系统', 104, 108),
  ('任务场景', '海军无人系统', 112, 118),
  ('性能指标', '航行器管理', 123, 128),
  ('性能指标', '任务计划', 129, 133),
  ('性能指标', '任务管理能力', 134, 140)],
 [('试验要素', '可重复使用运载火箭项目', 2, 13),
  ('性能指标', '垂直降落', 18, 22),
  ('系统组成', '第一级', 23, 26),
  ('系统组成', '回收主发动机', 27, 33),
  ('试验要素', '“南半球运载火箭”项目', 40, 51),
  ('任务场景', '发射成本', 58, 62),
  ('试验要素', '不同方案', 63, 67),
  ('试验要素', '飞行试验', 69, 73),


观察结果

v1:all

In [74]:
for sen, true, pre in zip(sentences, y_true, y_pre):
    print("".join(sen))
    print('-*-'*40)
    # 真实标签里有而预测结果里没有的（影响Recall）
    print(sorted(list(set(true).difference(set(pre))), key=lambda x: x[2]))
    print('-*-'*40)
    # 预测结果里有而真实标签里没有的（影响Precision）
    print(sorted(list(set(pre).difference(set(true))), key=lambda x: x[2]))
    print('-*-'*40)
    print(sorted(true, key=lambda x: x[2]))
    print('-*-'*40)
    print(sorted(pre, key=lambda x: x[2]))
    print('\n')

印度海军近日从“加尔各答”级驱逐舰上试射了由印度和以色列联合研制的远程面空导弹?试验在位于印度西海岸的“加尔各答”级驱逐舰上进行?试验中,该导弹成功拦截了一个增程型空中目标?此次试验的“巴拉克”-8导弹由印度国防研究与发展局?以色列航空工业公司?以色列武器研发与技术基础设施管理局?埃尔塔系统公司?拉法尔公司等机构联合研制?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“巴拉克”-8导弹', 92, 101)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“加尔各答”级驱逐舰', 7, 17), ('试验要素', '远程面空导弹', 33, 39), ('试验要素', '增程型空中目标', 79, 86), ('试验要素', '“巴拉克”-8导弹', 92, 101)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“加尔各答”级驱逐舰', 7, 17), ('试验要素', '远程面空导弹', 33, 39), ('试验要素', '增程型空中目标', 79, 86)]


美国空军24日在华盛顿州成功完成波音KC-46A加油机(工程与制造第2阶段)首次空中加油试验,开启了空中加油演示验证的里程碑C阶段?作为开发的一部分,试验小组完成了一系列试验,然后在波音机场为时5小时45分钟的

v2:vocab


In [106]:
for sen, true, pre in zip(sentences, y_true, y_pre):
    print("".join(sen))
    print('-*-'*40)
    # 真实标签里有而预测结果里没有的（影响Recall）
    print(sorted(list(set(true).difference(set(pre))), key=lambda x: x[2]))
    print('-*-'*40)
    # 预测结果里有而真实标签里没有的（影响Precision）
    print(sorted(list(set(pre).difference(set(true))), key=lambda x: x[2]))
    print('-*-'*40)
    print(sorted(true, key=lambda x: x[2]))
    print('-*-'*40)
    print(sorted(pre, key=lambda x: x[2]))
    print('\n')

印度海军近日从“加尔各答”级驱逐舰上试射了由印度和以色列联合研制的远程面空导弹?试验在位于印度西海岸的“加尔各答”级驱逐舰上进行?试验中,该导弹成功拦截了一个增程型空中目标?此次试验的“巴拉克”-8导弹由印度国防研究与发展局?以色列航空工业公司?以色列武器研发与技术基础设施管理局?埃尔塔系统公司?拉法尔公司等机构联合研制?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“巴拉克”-8导弹', 92, 101)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“加尔各答”级驱逐舰', 7, 17), ('试验要素', '远程面空导弹', 33, 39), ('试验要素', '增程型空中目标', 79, 86), ('试验要素', '“巴拉克”-8导弹', 92, 101)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“加尔各答”级驱逐舰', 7, 17), ('试验要素', '远程面空导弹', 33, 39), ('试验要素', '增程型空中目标', 79, 86)]


美国空军24日在华盛顿州成功完成波音KC-46A加油机(工程与制造第2阶段)首次空中加油试验,开启了空中加油演示验证的里程碑C阶段?作为开发的一部分,试验小组完成了一系列试验,然后在波音机场为时5小时45分钟的

v3:better

In [111]:
for sen, true, pre in zip(sentences, y_true, y_pre):
    print("".join(sen))
    print('-*-'*40)
    # 真实标签里有而预测结果里没有的（影响Recall）
    print(sorted(list(set(true).difference(set(pre))), key=lambda x: x[2]))
    print('-*-'*40)
    # 预测结果里有而真实标签里没有的（影响Precision）
    print(sorted(list(set(pre).difference(set(true))), key=lambda x: x[2]))
    print('-*-'*40)
    print(sorted(true, key=lambda x: x[2]))
    print('-*-'*40)
    print(sorted(pre, key=lambda x: x[2]))
    print('\n')

印度海军近日从“加尔各答”级驱逐舰上试射了由印度和以色列联合研制的远程面空导弹?试验在位于印度西海岸的“加尔各答”级驱逐舰上进行?试验中,该导弹成功拦截了一个增程型空中目标?此次试验的“巴拉克”-8导弹由印度国防研究与发展局?以色列航空工业公司?以色列武器研发与技术基础设施管理局?埃尔塔系统公司?拉法尔公司等机构联合研制?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“巴拉克”-8导弹', 92, 101)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“加尔各答”级驱逐舰', 7, 17), ('试验要素', '远程面空导弹', 33, 39), ('试验要素', '增程型空中目标', 79, 86), ('试验要素', '“巴拉克”-8导弹', 92, 101)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“加尔各答”级驱逐舰', 7, 17), ('试验要素', '远程面空导弹', 33, 39), ('试验要素', '增程型空中目标', 79, 86)]


美国空军24日在华盛顿州成功完成波音KC-46A加油机(工程与制造第2阶段)首次空中加油试验,开启了空中加油演示验证的里程碑C阶段?作为开发的一部分,试验小组完成了一系列试验,然后在波音机场为时5小时45分钟的

## 测试集结果

In [362]:
import pandas as pd

In [363]:
df = pd.read_excel('./difference_human.xlsx', index_col=0)

In [366]:
~df['Unnamed: 7'].isna()

0       True
1       True
2       True
3       True
4       True
       ...  
104    False
105    False
106    False
107    False
108    False
Name: Unnamed: 7, Length: 109, dtype: bool

In [367]:
df = df[['text', 'Unnamed: 7']][~df['Unnamed: 7'].isna()]

In [368]:
df.columns = ['text', 'tag']

In [369]:
df

text  \
0    高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型...   
1    美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系...   
2    “宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(M...   
3    俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机...   
4    2月,在美军联合能力技术演示验证计划支持下,美国陆军的坦克汽车研发与工程中心承担了一个为期3...   
..                                                 ...   
96   瑞典萨博公司研制的新型电子攻击干扰吊舱（EAJP）在新型鹰狮（Gripen）战机上进行了首次...   
97   美国陆军计划为其安全部队提供RQ-11B“渡鸦”式（Raven）小型无人机。“渡鸦”是一款完...   
98   在不久前进行的试验中，前哨无人机性能再次得到验证。前哨无人机是俄罗斯基于以色列搜寻者-MK2...   
99   轮式货物运送系统试验由陆军作战试验司令部空降与特种作战试验分部组织,第82空降师第2战斗旅第...   
100  1月26日,洛克希德--马丁公司在白沙导弹靶场进行了一次微型撞击杀伤导弹受控飞行试验,演示了...   

                                                   tag  
0    [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '...  
1    [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟...  
2    [('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13), ('任务场景', '战...  
3    [('试验要素', '无人侦察支队', 8, 13), ('试验要素', '“前哨-R”无人...  
4    [('试验要素', '“僚机项目”', 50, 55), ('任务场景', '士兵', 68...  
..                                                 ...  
96   [('试验要素', '新型电子攻击干扰吊舱（EAJP）', 10, 25), ('试验要素'...  
97   [('试验要素', 'RQ-11B“渡鸦”式（Raven）小型无人机', 15, 37), ...  
98   [('试验要素', '搜寻者-MK2无人机', 40, 49), ('任务场景', '侦查任...  
99   [('试验要素', '轮式货物运送系统试验', 1, 10), ('试验要素', '战术',...  
100  [('试验要素', '微型撞击杀伤导弹受控飞行试验', 29, 42), ('系统组成', ...  

[96 rows x 2 columns]

In [370]:
text = df.text.to_list()

In [371]:
tag = [eval(tag.replace('\xa0','')) for tag in df.tag.to_list()]

In [372]:
tag

[[('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25),
  ('试验要素', '目标跟踪数据', 27, 32),
  ('试验要素', '综合防空反导系统（IAMD）', 40, 53),
  ('系统组成', '战斗指挥系统（IBCS）', 55, 66),
  ('性能指标', '多域作战能力', 79, 84),
  ('性能指标', '陆军综合防空反导能力', 92, 101),
  ('试验要素', '机载和地面战斗指挥系统', 127, 137),
  ('试验要素', '信息', 139, 140),
  ('试验要素', '综合防空反导系统', 144, 151),
  ('任务场景', '隐形战机', 162, 165)],
 [('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13),
  ('任务场景', '战区级弹道导弹', 24, 30),
  ('任务场景', '短程(SRBM)', 33, 40),
  ('试验要素', '准中程(MRBM)', 42, 50),
  ('试验要素', '中程弹道导弹(IRBM)', 52, 63),
  ('系统组成', '雷达', 90, 91),
  ('试验要素', '跟踪数据', 96, 99),
  ('任务场景', '洲际导弹导弹', 112, 117),
  ('任务场景', '防御系统', 119, 122)],
 [('试验要素', '无人侦察支队', 8, 13),
  ('试验要素', '“前哨-R”无人机', 19, 27),
  ('试验要素', '“牵牛星”无人机', 39, 46),
  ('性能指标',

In [373]:
hum = {s:t for s,t in zip(text, tag)}

In [376]:
re = []
for sen, true in zip(sentences, y_true):
#     print(''.join(sen))
#     print(t)
    if ''.join(sen) in hum.keys():
        re.append(hum[''.join(sen)])
#         print('in')
    else:
        re.append(true)

In [377]:
re

[[],
 [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [],
 [],
 [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25),
  ('试验要素', '目标跟踪数据', 27, 32),
  ('试验要素', '综合防空反导系统（IAMD）', 40, 53),
  ('系统组成', '战斗指挥系统（IBCS）', 55, 66),
  ('性能指标', '多域作战能力', 79, 84),
  ('性能指标', '陆军综合防空反导能力', 92, 101),
  ('试验要素', '机载和地面战斗指挥系统', 127, 137),
  ('试验要素', '信息', 139, 140),
  ('试验要素', '综合防空反导系统', 144, 151),
  ('任务场景', '隐形战机', 162, 165)],
 [('试验要素', '液体冲压发动机相关试验', 14, 24),
  ('试验要素', '“锆石”高超声速导弹移动发射装置', 37, 52),
  ('试验要素', '动力装置', 114, 117)],
 [('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13),
  ('任务场景', '战区级弹道导弹', 24, 30),
  ('任务场景', '短程(SRBM)', 33, 40),
  ('试验要素', '准中程(MRBM)', 42, 50),
  ('试验要素', '中程弹道导弹(IRBM)', 52, 63),
  ('系统组成', '雷达', 90, 91),
  ('试验要素', '跟踪数据', 96, 99),
  ('任务场景', '洲际导弹导弹', 112, 117),
  ('任务场景', '防御

In [378]:
submit = {}
for idx, sample in enumerate(re):
    sample_list = []
    for entity in sample:
        enti_dict = {
            "label_type": entity[0],
            "overlap": 0,
            "start_pos": entity[2],
            "end_pos": entity[3]
        }
        sample_list.append(enti_dict)
    submit[f"test_{idx + 1}.json"] = sample_list

with open('./fusion_submit_hhh_v2.json', 'w', encoding='utf-8') as f_sub:
    # convert dict to json
    json_data = json.dumps(submit, indent=4, ensure_ascii=False)
    f_sub.write(json_data)

In [2]:
from pathlib import Path

In [399]:
ex1_dir = Path('../ensemble/ex29')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_pre.append(sample)

In [37]:
ex1_dir = Path('../ensemble/ex42')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_true = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_true.append(sample)

In [394]:
import pandas as pd

In [39]:
text = []
all_70 = []
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print('70.7:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
#         print('69:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
#         print('70.7:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
#         print('69:',sorted(pre, key=lambda p: p[2]))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(true, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'all_70':all_70
})
df.to_excel('./b_test_70.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-

69 vs 70

In [295]:
text = []
in_70 = []
in_69 = []
all_70 = []
all_69 = []
for sen, pre, true in zip(sentences, y_pre, y_true):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true)))!=[]):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('70.7:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('69:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('70.7:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('69:',sorted(pre, key=lambda p: p[2]))
        print('\n')
        text.append("".join(sen))
        in_70.append(list(set(true).difference(set(pre))))
        in_69.append(list(set(pre).difference(set(true))))
        all_70.append(sorted(true, key=lambda p: p[2]))
        all_69.append(sorted(pre, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'difference_70':in_70,
    'difference_69':in_69,
    'all_70':all_70,
    'all_69':all_69
})
# df.to_excel('./difference.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
70.7: [('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
69: [('任务场景', '高精确?低空飞行目标', 81, 90)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
70.7: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
69: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('

In [175]:
ex1_dir = Path('../ensemble')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_true = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_true.append(sample)

In [163]:
test_data_dir = Path('../data/fold0/test/')
with open(test_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen:
#     open(val_data_dir/'tags.txt', 'r', encoding='utf-8') as f_tag:
    sentences = [line.strip().split(' ') for line in f_sen]
#     tags = [line.strip().split(' ') for line in f_tag]

In [205]:
ex1_dir = Path('../ensemble/ex22')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_pre.append(sample)

In [202]:
y_pre

[[('试验要素', 'N', 1, 12),
  ('系统组成', '', 30, 34),
  ('性能指标', '', 46, 49),
  ('系统组成', '', 53, 56),
  ('系统组成', '', 38, 41),
  ('性能指标', '', 38, 41),
  ('性能指标', '', 70, 77),
  ('系统组成', '', 59, 62),
  ('系统组成', '', 20, 22),
  ('性能指标', '', 40, 41),
  ('系统组成', '', 43, 44)],
 [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('性能指标', '', 59, 62),
  ('系统组成', '', 47, 50),
  ('系统组成', '', 115, 118),
  ('试验要素', '', 59, 62),
  ('任务场景', '', 131, 134),
  ('系统组成', '', 6, 9),
  ('系统组成', '', 23, 26),
  ('系统组成', '', 87, 90),
  ('系统组成', '', 12, 15),
  ('性能指标', '', 102, 103),
  ('系统组成', '', 93, 96),
  ('试验要素', '', 136, 138)],
 [('系统组成', '', 81, 83),
  ('试验要素', '', 2, 13),
  ('性能指标', '', 123, 127),
  ('性能指标', '', 91, 95),
  ('性能指标', '', 86, 89),
  ('试验要素', '', 63, 74),
  ('系统组成', '', 20

In [203]:
for sen, pre in zip(sentences, y_pre):
    if "".join(sen) != 'N':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
    #     print(list(set(true).difference(set(pre))))
    #     print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
    #     print(list(set(pre).difference(set(true))))
    #     print('-*-'*40)
    #     print(true)
    #     print('-*-'*40)
        print(sorted(pre, key=lambda p: p[2]))
        print('\n')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟踪数据', 27, 32), ('试验要素', '综合防空反导系统（IAMD）', 40, 53), ('系统组成', '战斗指挥系统（IBCS）', 55, 66), ('性能指标', '多域作战能力', 79, 84), ('性能指标', '陆军综合防空反导能力', 92, 101), ('试验要素', '机载和地面战

In [204]:
ex1_dir = Path('../ensemble/ex20')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_true = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_true.append(sample)

In [293]:
for sen, pre, true in zip(sentences, y_pre, y_true):
    if "".join(sen) != 'N':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print(sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print(sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print(sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print(sorted(pre, key=lambda p: p[2]))
        print('\n')

﻿RT-2PM2弹道导弹的主要改进是在分系统应用了更先进的固体发动机、具有特殊弹道的弹头、命中精度更高的制导系统以及快速发射等新技术成果，战术技术性能指标明显提高。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]


高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('任务场景', '高



﻿22350型护卫舰是俄罗斯海军隶下的中型防空导弹护卫舰，排水量4500吨左右，主桅杆安装四面固定式多功能相控阵雷达，为舰首28单元鲁道特导弹垂直发射装置发射导弹提供制导，主桅杆顶端安装一具旋转式三维搜索相控阵雷达，舰首装备一门130毫米舰炮，并将反舰导弹装填于鲁道特后方的另一种垂直发射装置中，可装填16枚红宝石或布拉莫斯反舰导弹，舰体设计刚毅简洁，整体配置布局紧凑，综合火力强大。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[]




In [199]:
ex1_dir = Path('../ensemble')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_pre.append(sample)

In [200]:
for sen, pre in zip(sentences, y_pre):
    if "".join(sen) != 'N':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
    #     print(list(set(true).difference(set(pre))))
    #     print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
    #     print(list(set(pre).difference(set(true))))
    #     print('-*-'*40)
    #     print(true)
    #     print('-*-'*40)
        print(sorted(pre, key=lambda p: p[2]))
        print('\n')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('性能指标', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
[('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟踪数据', 27, 32), ('试验要素', '综合防空反导系统（IAMD）', 40, 53), ('系统组成', '战斗指挥系统（IBCS）', 55, 66), ('试验要素', 'F-35战机', 72, 77), ('性能指标', '多域作战能力', 79

70 vs 71

## 规则

1. 如果出现两个相同实体，先选前面那个
2. 出现单个成对标点，删除该实体
3. 实体长度为1
4. 前面出现过的缩写不抽
5. xxx的xx,补“的”

In [20]:
from pathlib import Path

In [18]:
from collections import Counter

In [12]:
test_data_dir = Path('../data/fold0/test/')
with open(test_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen:
    sentences = [line.strip().split(' ') for line in f_sen]

In [13]:
ex1_dir = Path('../ensemble/ex11')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'validate_V2_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos']-1, entity['end_pos']-1))
    y_pre.append(sample)

In [14]:
y_pre

[[('试验要素', 'F-35战斗机', 25, 31),
  ('系统组成', 'F-35战斗机系统', 44, 52),
  ('试验要素', 'F-35战斗机系统', 44, 52),
  ('试验要素', 'F-35B战斗机', 62, 69),
  ('系统组成', '轮胎', 70, 71),
  ('试验要素', 'F-35B', 79, 83),
  ('试验要素', 'F-35C战斗机', 85, 92),
  ('系统组成', '空中受油头锥', 94, 99),
  ('试验要素', 'F-35A战斗机', 109, 116),
  ('试验要素', '机炮射击精度', 118, 123),
  ('性能指标', '可靠性指标', 147, 151),
  ('试验要素', '可靠性指标', 147, 151)],
 [('试验要素', '国家网络靶场(NCR)', 37, 47),
  ('试验要素', '例行维护和能力提升项目', 53, 63),
  ('任务场景', '网络战技术', 85, 89),
  ('试验要素', '网络战技术', 85, 89),
  ('试验要素', '网络协议', 133, 136),
  ('任务场景', '网络协议', 133, 136),
  ('任务场景', '卫星和射频通信系统', 138, 146),
  ('系统组成', '卫星和射频通信系统', 138, 146),
  ('试验要素', '卫星和射频通信系统', 138, 146),
  ('系统组成', '战术机动通信', 149, 154),
  ('任务场景', '战术机动通信', 149, 154),
  ('试验要素', '战术机动通信和海事通信系统', 149, 161),
  ('任务场景', '海事通信系统', 156, 161)],
 [('试验要素', '国家太空防御中心', 9, 16),
  ('试验要素', '试验性机构', 18, 22),
  ('任务场景', '试验性机构', 18, 22),
  ('任务场景', '全天候', 27, 29),
  ('试验要素', '全天候运行', 27, 31),
  ('性能指标', '全天候运行', 27, 31),
  ('性能指标', '全天候', 27, 

rule_1: 如果出现两个相同实体，先选前面那个

In [109]:
def rule_1(entities):
    """如果单样本出现两个相同实体，先选前面那个
    Args:
        entities (List[Tuple]): [('试验要素', '可靠性指标', 147, 151),]

    Returns:

    """
    result = []
    # 按start索引降序排列
    entities = sorted(entities, key=lambda en: en[-2], reverse=True)
    for idx in range(len(entities)):
        # 取靠前实体
        front_en = entities.pop()
        result.append(front_en)
        # 保存tmp
        tmp_entis = copy.deepcopy(entities)
        # 遍历当前实体后面的实体
        for next_en in entities:
            # 如果后面的实体与当前实体类别和内容相同，则删除
            if next_en[:2] == front_en[:2]:
                tmp_entis.remove(next_en)
        entities = tmp_entis
        if len(entities) == 0:
            break
    return result

In [110]:
import copy

In [111]:
entities = [('系统组成', 'F-35战斗机系统', 3, 8),
  ('系统组成', '轮胎',4,11),
  ('系统组成', '机炮',8,20),
  ('试验要素', '可靠性指标',11,22),
 ('系统组成', 'F-35战斗机系统',5,10)]

In [112]:
rule_1(entities)

[('系统组成', 'F-35战斗机系统', 3, 8),
 ('系统组成', '轮胎', 4, 11),
 ('系统组成', '机炮', 8, 20),
 ('试验要素', '可靠性指标', 11, 22)]

In [95]:
new_entis

[('系统组成', 'F-35战斗机系统', 3, 8),
 ('系统组成', '轮胎', 4, 11),
 ('系统组成', '机炮', 8, 20),
 ('试验要素', '可靠性指标', 11, 22)]

In [85]:
new_y_pre = []
for entities in y_pre:
    new_entis = []
    # 按start索引降序排列
    entities = sorted(entities, key=lambda en: en[-2], reverse=True)  
    for idx in range(len(entities)):
        # 取靠前实体
        front_en = entities.pop()
        new_entis.append(front_en)
        # 保存tmp
        tmp_entis = copy.deepcopy(entities)
        # 遍历当前实体后面的实体
        for next_en in entities:
            # 如果后面的实体与当前实体类别和内容相同，则删除
            if next_en[:2] == front_en[:2]:
                tmp_entis.remove(next_en)
        entities = tmp_entis
        if len(entities) == 0:
            new_y_pre.append(new_entis)
            break
    else:
        new_y_pre.append(new_entis)

In [86]:
new_y_pre

[[('试验要素', 'F-35战斗机', 25, 31),
  ('系统组成', 'F-35战斗机系统', 44, 52),
  ('试验要素', 'F-35B战斗机', 62, 69),
  ('系统组成', '轮胎', 70, 71),
  ('试验要素', 'F-35B', 79, 83),
  ('试验要素', 'F-35C战斗机', 85, 92),
  ('系统组成', '空中受油头锥', 94, 99),
  ('试验要素', 'F-35A战斗机', 109, 116),
  ('系统组成', '机炮', 118, 119),
  ('性能指标', '射击精度', 120, 123),
  ('试验要素', '可靠性指标', 147, 151)],
 [('试验要素', '国家网络靶场(NCR)', 37, 47),
  ('试验要素', '例行维护和能力提升项目', 53, 63),
  ('试验要素', '能力提升项目', 58, 63),
  ('任务场景', '网络战技术', 85, 89),
  ('试验要素', '网络协议', 133, 136),
  ('试验要素', '卫星和射频通信系统', 138, 146),
  ('试验要素', '战术机动通信和海事通信系统', 149, 161)],
 [('试验要素', '国家太空防御中心', 9, 16),
  ('试验要素', '试验性机构', 18, 22),
  ('性能指标', '全天候运行', 27, 31),
  ('任务场景', '作战中心', 33, 36),
  ('任务场景', '美国关键太空资产', 46, 53),
  ('任务场景', '美国太空能力', 57, 62),
  ('任务场景', '潜在威胁', 66, 69),
  ('性能指标', '全天候', 84, 86),
  ('任务场景', '太空领域', 96, 99),
  ('任务场景', '信息共享', 101, 104),
  ('任务场景', '国家安全空间企业级体系', 110, 120),
  ('任务场景', '新兴和先进', 125, 129),
  ('任务场景', '太空威胁', 131, 134),
  ('任务场景', '美军', 149, 150),
  ('任务场景', 

In [96]:
# write to json file
submit = {}
for idx, entities in enumerate(new_y_pre):
    sample_list = []
    for entity in set(entities):
        enti_dict = {}
        enti_dict["label_type"] = entity[0]
        enti_dict["overlap"] = 0
        enti_dict["start_pos"] = entity[2]+1
        enti_dict["end_pos"] = entity[3]+1
        sample_list.append(enti_dict)
    submit[f"validate_V2_{idx + 1}.json"] = sample_list

with open('./rule_1_submit.json', 'w', encoding='utf-8') as f_sub:
    # convert dict to json
    json_data = json.dumps(submit, indent=4, ensure_ascii=False)
    f_sub.write(json_data)

In [102]:
ex1_dir = Path('../ensemble')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'validate_V2_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos']-1, entity['end_pos']-1))
    y_pre.append(sample)

In [103]:
y_pre

[[('试验要素', '可靠性指标', 147, 151),
  ('系统组成', '空中受油头锥', 94, 99),
  ('性能指标', '射击精度', 120, 123),
  ('系统组成', '系统', 51, 52),
  ('系统组成', '机炮', 118, 119),
  ('试验要素', 'F-35B战斗机', 62, 69),
  ('系统组成', '轮胎', 70, 71),
  ('试验要素', 'F-35C战斗机', 85, 92),
  ('试验要素', 'F-35B', 79, 83),
  ('试验要素', 'F-35战斗机', 25, 31)],
 [('试验要素', '卫星和射频通信系统', 138, 146),
  ('试验要素', '战术机动通信和海事通信系统', 149, 161),
  ('任务场景', '网络战技术', 85, 89),
  ('试验要素', '国家网络靶场(NCR)', 37, 47),
  ('任务场景', '国家网络靶场', 68, 73),
  ('试验要素', '能力提升项目', 58, 63),
  ('试验要素', '网络协议', 133, 136),
  ('试验要素', '例行维护和能力提升项目', 53, 63)],
 [('任务场景', '国家安全空间企业级体系', 110, 120),
  ('试验要素', '国家太空防御中心', 9, 16),
  ('试验要素', '试验性机构', 18, 22),
  ('任务场景', '美国太空能力', 57, 62),
  ('任务场景', '美国关键太空资产', 46, 53),
  ('任务场景', '新兴和先进', 125, 129),
  ('性能指标', '全天候运行', 27, 31),
  ('任务场景', '美国及联合作战人员', 157, 165),
  ('任务场景', '美军', 149, 150),
  ('任务场景', '太空领域', 171, 174),
  ('任务场景', '太空威胁', 131, 134),
  ('任务场景', '信息共享', 101, 104),
  ('性能指标', '全天候', 84, 86),
  ('任务场景', '潜在威胁', 66, 69),
  ('任务场景', '太

In [99]:
new_y_pre = []
for entities in y_pre:
    new_entis = []
    # 按start索引降序排列
    entities = sorted(entities, key=lambda en: en[-2], reverse=True)  
    for idx in range(len(entities)):
        
        # 取靠前实体
        front_en = entities.pop()
        new_entis.append(front_en)
        # 保存tmp
        tmp_entis = copy.deepcopy(entities)
        # 遍历当前实体后面的实体
        for next_en in entities:
            # 如果后面的实体与当前实体类别和内容相同，则删除
            if next_en[:2] == front_en[:2]:
                tmp_entis.remove(next_en)
        entities = tmp_entis
        if len(entities) == 0:
            new_y_pre.append(new_entis)
            break
    else:
        new_y_pre.append(new_entis)

In [100]:
new_y_pre

[[('试验要素', 'F-35战斗机', 25, 31),
  ('系统组成', '轮胎', 70, 71),
  ('试验要素', 'F-35B', 79, 83),
  ('试验要素', 'F-35C战斗机', 85, 92),
  ('系统组成', '空中受油头锥', 94, 99),
  ('系统组成', '机炮', 118, 119),
  ('性能指标', '射击精度', 120, 123),
  ('试验要素', '可靠性指标', 147, 151)],
 [('试验要素', '国家网络靶场(NCR)', 37, 47),
  ('试验要素', '例行维护和能力提升项目', 53, 63),
  ('任务场景', '网络战技术', 85, 89),
  ('试验要素', '网络协议', 133, 136),
  ('试验要素', '卫星和射频通信系统', 138, 146),
  ('试验要素', '战术机动通信和海事通信系统', 149, 161)],
 [('试验要素', '国家太空防御中心', 9, 16),
  ('试验要素', '试验性机构', 18, 22),
  ('性能指标', '全天候', 27, 29),
  ('任务场景', '作战中心', 33, 36),
  ('任务场景', '美国关键太空资产', 46, 53),
  ('任务场景', '美国太空能力', 57, 62),
  ('任务场景', '潜在威胁', 66, 69),
  ('任务场景', '太空领域', 96, 99),
  ('任务场景', '信息共享', 101, 104),
  ('任务场景', '国家安全空间企业级体系', 110, 120),
  ('任务场景', '新兴和先进', 125, 129),
  ('任务场景', '太空威胁', 131, 134),
  ('任务场景', '美军', 149, 150),
  ('任务场景', '美国及联合作战人员', 157, 165)],
 [('试验要素', '“巨型钻地弹”(MOP)', 13, 24),
  ('任务场景', '常规炸弹', 53, 56),
  ('试验要素', '列编项目', 66, 69),
  ('试验要素', '“巨型钻地弹”空投试验', 111, 121)],
 [(

In [101]:
# write to json file
submit = {}
for idx, entities in enumerate(new_y_pre):
    sample_list = []
    for entity in set(entities):
        enti_dict = {}
        enti_dict["label_type"] = entity[0]
        enti_dict["overlap"] = 0
        enti_dict["start_pos"] = entity[2]+1
        enti_dict["end_pos"] = entity[3]+1
        sample_list.append(enti_dict)
    submit[f"validate_V2_{idx + 1}.json"] = sample_list

with open('./rule_1_submit_ex2.json', 'w', encoding='utf-8') as f_sub:
    # convert dict to json
    json_data = json.dumps(submit, indent=4, ensure_ascii=False)
    f_sub.write(json_data)

实体词典

In [403]:
with open('./en_freq.txt', 'r', encoding='utf-8') as f:
    entities = [line.strip().split('\t') for line in f]

In [410]:
df = pd.DataFrame({
    "type": [en[0] for en in entities],
    "content": [en[1] for en in entities],
    "freq": [en[-1] for en in entities]
})

In [411]:
df

type     content freq
0     性能指标          射程   43
1     试验要素        飞行试验   33
2     性能指标           重   14
3     性能指标          速度   13
4     试验要素         无人机   12
...    ...         ...  ...
2670  性能指标        持续时间    1
2671  试验要素  高空“伪卫星”无人机    1
2672  系统组成       通信中继器    1
2673  系统组成      拍照录像设备    1
2674  系统组成        气象设备    1

[2675 rows x 3 columns]

In [413]:
g = df.groupby('type')

In [444]:
ty_exp = df.iloc[g.groups['系统组成']].content.tolist()

In [437]:
import re

In [438]:
# 任务场景少
for t in ty_exp:
    pat = re.findall(r'\([a-zA-Z0-9]+\)', t)
    if pat != []:
        print(pat)

['(ADF)']


In [445]:
# 性能指标少
for t in ty_exp:
    pat = re.findall(r'“.+”', t)
    if pat != []:
        print(pat)

['“套”']
['“毕业季光电侦察系统”']
['“连接器后壳”']
['“多任务发射器”']
['“阿什温”']
['“大地”']
['“通用数据链路”']
['“活性区”']
['“✈主燃烧室”']
['“✈热等静压”']
['“光束”']


test_set

In [462]:
from itertools import chain
test = list(chain(*y_true))

In [463]:
df_test = pd.DataFrame({
    "type": [en[0] for en in test],
    "content": [en[1] for en in test]
})

In [464]:
df_g = df_test.groupby('type')

In [467]:
ty_exp = df_test.iloc[df_g.groups['任务场景']].content.tolist()

In [466]:
# 性能指标少
for t in ty_exp:
    pat = re.findall(r'“.+”', t)
    if pat != []:
        print(pat)

['“任务破坏”']
['“导弹破坏”']
['“黑障区”']
['“碰撞杀伤”']
['“碰撞-杀伤”']


In [468]:
# 任务场景少
for t in ty_exp:
    pat = re.findall(r'\([a-zA-Z0-9]+\)', t)
    if pat != []:
        print(pat)

['(SRBM)']
['(MRBM)']
['(IRBM)']
['(EASR)']


In [36]:
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('-*-'*40)
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('\n')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-

In [50]:
y_true

[[('系统组成', '制导系统', 53, 56),
  ('系统组成', '特殊弹道', 38, 41),
  ('性能指标', '战术技术性能指标', 70, 77),
  ('系统组成', '固体发动机', 30, 34),
  ('系统组成', '弹头', 43, 44),
  ('系统组成', '分系统', 20, 22),
  ('性能指标', '特殊弹道', 38, 41),
  ('试验要素', '\ufeffRT-2PM2弹道导弹', 1, 12),
  ('性能指标', '战术技术性能', 70, 75),
  ('性能指标', '命中精度', 46, 49),
  ('系统组成', '快速发射', 59, 62)],
 [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('系统组成', '侧向喷嘴', 23, 26),
  ('系统组成', '侧向引擎', 6, 9),
  ('试验要素', '推力矢量', 47, 50),
  ('试验要素', '拦截点', 136, 138),
  ('系统组成', '小型引擎', 93, 96),
  ('系统组成', '推力矢量', 47, 50),
  ('系统组成', '弹体重心', 12, 15),
  ('系统组成', '侧向喷嘴', 115, 118),
  ('试验要素', '侧推力道', 59, 62),
  ('性能指标', '侧推力道', 59, 62)],
 [('性能指标', '硬目标', 131, 133),
  ('性能指标', '精度修正', 86, 89),
  ('性能指标', '精度', 106, 107),
  ('性能指标', '射程', 51, 52),
  ('

In [402]:
for sen, pre, true in zip(sentences, y_pre, y_true):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true)))!=[]):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')


“宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(MRBM)和中程弹道导弹(IRBM)?除了拦截战区级弹道导弹,“宙斯盾”弹道导弹防御系统雷达的探测和跟踪数据还可以传递给其他用于拦截洲际导弹导弹的防御系统?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '短程(SRBM)', 33, 40)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: []
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13), ('任务场景', '战区级弹道导弹', 24, 30), ('试验要素', '短程(SRBM)', 33, 40), ('任务场景', '短程(SRBM)', 33, 40), ('任务场景', '准中程(MRBM)', 42, 50), ('试验要素', '准中程(MRBM)', 42, 50), ('试验要素', '中程弹道导弹(IRBM)', 52, 63), ('任务场景', '中程弹道导弹(IRBM)', 52, 63), ('系统组成', '雷达', 90, 91), ('试验要素', '跟踪数据', 96, 99), ('任务场景', '洲际导弹导弹', 112, 117), ('任务场景', '防御系统', 119, 122)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--

In [21]:
from pathlib import Path

In [86]:
ex1_dir = Path('../ensemble/ex45')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_true = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_true.append(sample)

In [ ]:
for sen, pre, true in zip(sentences, y_pre, y_true):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true)))!=[]):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

In [87]:
import pandas as pd

In [43]:
tags = [eval(line) for line in pd.read_excel('./b_test_70_v2.xlsx', index_col=0)['all_70'].tolist()]

In [27]:
y_true

[[('系统组成', '制导系统', 53, 56),
  ('系统组成', '特殊弹道', 38, 41),
  ('性能指标', '战术技术性能指标', 70, 77),
  ('系统组成', '固体发动机', 30, 34),
  ('系统组成', '弹头', 43, 44),
  ('系统组成', '分系统', 20, 22),
  ('性能指标', '特殊弹道', 38, 41),
  ('试验要素', '\ufeffRT-2PM2弹道导弹', 1, 12),
  ('性能指标', '战术技术性能', 70, 75),
  ('性能指标', '命中精度', 46, 49),
  ('系统组成', '快速发射', 59, 62)],
 [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('系统组成', '侧向喷嘴', 23, 26),
  ('系统组成', '侧向引擎', 6, 9),
  ('试验要素', '推力矢量', 47, 50),
  ('试验要素', '拦截点', 136, 138),
  ('系统组成', '小型引擎', 93, 96),
  ('系统组成', '推力矢量', 47, 50),
  ('系统组成', '弹体重心', 12, 15),
  ('系统组成', '侧向喷嘴', 115, 118),
  ('试验要素', '侧推力道', 59, 62),
  ('性能指标', '侧推力道', 59, 62)],
 [('性能指标', '硬目标', 131, 133),
  ('性能指标', '精度修正', 86, 89),
  ('性能指标', '精度', 106, 107),
  ('性能指标', '射程', 51, 52),
  ('

In [32]:
tags

[[('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25),
  ('试验要素', '目标跟踪数据', 27, 32),
  ('系统组成', '战斗指挥系统（IBCS）', 55, 66),
  ('试验要素', '战斗指挥系统（IBCS）', 55, 66),
  ('性能指标', '多域作战能力', 79, 84),
  ('任务场景', '陆军', 92, 93),
  ('性能指标', '综合防空反导能力', 94, 101),
  ('试验要素', '机载和地面战斗指挥系统', 127, 137),
  ('试验要素', '信息', 139, 140),
  ('试验要素', '综合防空反导系统', 144, 151),
  ('任务场景', '隐形战机', 162, 165)],
 [('试验要素', '液体冲压发动机相关试验', 14, 24),
  ('试验要素', '“锆石”高超声速导弹移动发射装置', 37, 52),
  ('试验要素', '动力装置', 114, 117)],
 [('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13),
  ('任务场景', '战区级弹道导弹', 24, 30),
  ('任务场景', '短程(SRBM)', 33, 40),
  ('任务场景', '准中程(MRBM)', 42, 50),
  ('任务场景', '中程弹道导弹(IRBM)', 52, 63),
  ('系统组成', '雷达', 90, 91),
  ('试验要素', '探测和跟踪数据', 93, 99),
  ('任务场景', '洲际导弹导弹', 112, 117),
  ('

In [46]:
new_pre = []
count = 0
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff' and count <=30:
#         print('in')
        new_pre.append(tags[count])
        count += 1
    else:
        new_pre.append(true)

In [47]:
new_pre

[[('系统组成', '制导系统', 53, 56),
  ('系统组成', '特殊弹道', 38, 41),
  ('性能指标', '战术技术性能指标', 70, 77),
  ('系统组成', '固体发动机', 30, 34),
  ('系统组成', '弹头', 43, 44),
  ('系统组成', '分系统', 20, 22),
  ('性能指标', '特殊弹道', 38, 41),
  ('试验要素', '\ufeffRT-2PM2弹道导弹', 1, 12),
  ('性能指标', '战术技术性能', 70, 75),
  ('性能指标', '命中精度', 46, 49),
  ('系统组成', '快速发射', 59, 62)],
 [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('系统组成', '侧向喷嘴', 23, 26),
  ('系统组成', '侧向引擎', 6, 9),
  ('试验要素', '推力矢量', 47, 50),
  ('试验要素', '拦截点', 136, 138),
  ('系统组成', '小型引擎', 93, 96),
  ('系统组成', '推力矢量', 47, 50),
  ('系统组成', '弹体重心', 12, 15),
  ('系统组成', '侧向喷嘴', 115, 118),
  ('试验要素', '侧推力道', 59, 62),
  ('性能指标', '侧推力道', 59, 62)],
 [('性能指标', '硬目标', 131, 133),
  ('性能指标', '精度修正', 86, 89),
  ('性能指标', '精度', 106, 107),
  ('性能指标', '射程', 51, 52),
  ('

In [49]:
submit = {}
for idx, sample in enumerate(new_pre):
    sample_list = []
    for entity in sample:
        enti_dict = {
            "label_type": entity[0],
            "overlap": 0,
            "start_pos": entity[2],
            "end_pos": entity[3]
        }
        sample_list.append(enti_dict)
    submit[f"test_{idx + 1}.json"] = sample_list

with open('./fusion_submit_hhh_v4.json', 'w', encoding='utf-8') as f_sub:
    # convert dict to json
    json_data = json.dumps(submit, indent=4, ensure_ascii=False)
    f_sub.write(json_data)

## human

In [122]:
test_data_dir = Path('../data/fold0/test/')
with open(test_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen:
    sentences = [line.strip().split(' ') for line in f_sen]

71

In [123]:
ex1_dir = Path('../ensemble/ex42')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_true = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_true.append(sample)

70

In [100]:
ex1_dir = Path('../ensemble/ex48')
import json
with open(ex1_dir/'fusion_submit_extra.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_pre.append(sample)

In [111]:
y_pre

[[('系统组成', '制导系统', 53, 56),
  ('系统组成', '特殊弹道', 38, 41),
  ('性能指标', '特殊弹道', 38, 41),
  ('系统组成', '固体发动机', 30, 34),
  ('系统组成', '弹头', 43, 44),
  ('系统组成', '分系统', 20, 22),
  ('性能指标', '战术技术性能指标', 70, 77),
  ('试验要素', '\ufeffRT-2PM2弹道导弹', 1, 12),
  ('性能指标', '战术技术性能', 70, 75),
  ('性能指标', '弹道', 40, 41),
  ('性能指标', '命中精度', 46, 49),
  ('系统组成', '快速发射', 59, 62)],
 [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('性能指标', '高精确', 81, 83),
  ('任务场景', '高精确', 81, 83),
  ('性能指标', '低空飞行目标', 85, 90),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('性能指标', '后方', 102, 103),
  ('系统组成', '侧向引擎', 6, 9),
  ('系统组成', '侧向喷嘴', 23, 26),
  ('试验要素', '侧推力道', 59, 62),
  ('性能指标', '侧推力道', 59, 62),
  ('试验要素', '拦截点', 136, 138),
  ('系统组成', '小型引擎', 93, 96),
  ('系统组成', '推力矢量', 47, 50),
  ('试验要素', '推力矢量', 47, 50),
  ('系统组成', '弹体重心', 12, 15),
  ('系统组成', '侧向喷嘴', 115, 118),
  ('系

In [116]:
test_data_dir = Path('../data/fold0/test/')
with open(test_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen:
    sentences = [line.strip().split(' ') for line in f_sen]

In [121]:
text = []
all_70 = []
for sen, pre in zip(sentences, y_pre):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(pre, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'all_70':all_70
})
df.to_excel('./b_test_71.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。


在阿尔罕格力斯克州靶场进行液体冲压发动机相关试验过程中发生的爆炸，可能与“锆石”高超声速导弹移动发射装置有关。“锆石”导弹的研制工作正在积极开展。按照机械制造科研生产联合体需求，在红军科研所靶场对“火星”科研生产联合体所制造的动力装置进行了试验。该事件发生后几小时，第45试验场附近的德维纳湾区域禁止船只通行1个月。


“宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(MRBM)和中程弹道导弹(IRBM)?除了拦截战区级弹道导弹,“宙斯盾”弹道导弹防御系统雷达的探测和跟踪数据还可以传递给其他用于拦截洲际导弹导弹的防御系统?


俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机。“前哨-R”无人机重450kg，飞行半径达250km，时速200km/h，主要用于执行侦察任务。“牵牛星”无人机巡航速度为150-250km/h，装备雷达、光学设备、无线电设备，可执行全频谱侦察任务，可携带1吨的有效载荷。无人机不仅可以进行侦察，还可以使用高精度导弹和炸弹执行打击任务，此外无人机可以与其他打击系统联合，综合运用包括“伊斯坎德尔”导弹在内的武器。


弹道导弹和巡航导弹可携带常规和非常规弹头?常规弹头依靠弹药的爆炸产生杀伤效果,非传统弹头主要指核?生物?化学等大规模杀伤性弹头,以及旨在使设备损坏的非致命弹头?常规?生物和化学武器可装在一个弹头或多个小型炸弹中在一定高度释放?


2月,在美军联合能力技术演示验证计划支持下,美国陆军的坦克汽车研发与工程中心承担了一个为期3年的✈“僚机项目”,其目的是开发出两套可由士兵控制的自主

In [115]:
entity={}
for p in y_pre:
    for ele in p:
        if ele[1:] not in entity:
            entity[ele[1:]]=set()
        entity[ele[1:]].add(ele[0])
count_1=count_2=count_3=0    
for key,value in entity.items():
    if '试验要素' in value and '任务场景' in value:
        count_1+=1
    if '试验要素' in value and '系统组成' in value:
        count_2+=1
    if '试验要素' in value and '性能指标' in value:
        count_3+=1
count_1,count_2,count_3

(255, 327, 151)

In [ ]:
text = []
all_70 = []
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(true, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'all_70':all_70
})
df.to_excel('./b_test_71.xlsx')

In [124]:
for sen, pre in zip(sentences, y_pre):
    if sen[0]!='\ufeff':
        print("".join(sen))
#         print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
#         print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
#         print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
#         print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')


高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('性能指标', '高精确', 81, 83), ('任务场景', '高精确', 81, 83), ('性能指标', '低空飞行目标', 85, 90), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*

In [53]:
text = []
all_70 = []
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(true, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'all_70':all_70
})
df.to_excel('./b_test_71.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。


在阿尔罕格力斯克州靶场进行液体冲压发动机相关试验过程中发生的爆炸，可能与“锆石”高超声速导弹移动发射装置有关。“锆石”导弹的研制工作正在积极开展。按照机械制造科研生产联合体需求，在红军科研所靶场对“火星”科研生产联合体所制造的动力装置进行了试验。该事件发生后几小时，第45试验场附近的德维纳湾区域禁止船只通行1个月。


“宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(MRBM)和中程弹道导弹(IRBM)?除了拦截战区级弹道导弹,“宙斯盾”弹道导弹防御系统雷达的探测和跟踪数据还可以传递给其他用于拦截洲际导弹导弹的防御系统?


俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机。“前哨-R”无人机重450kg，飞行半径达250km，时速200km/h，主要用于执行侦察任务。“牵牛星”无人机巡航速度为150-250km/h，装备雷达、光学设备、无线电设备，可执行全频谱侦察任务，可携带1吨的有效载荷。无人机不仅可以进行侦察，还可以使用高精度导弹和炸弹执行打击任务，此外无人机可以与其他打击系统联合，综合运用包括“伊斯坎德尔”导弹在内的武器。


弹道导弹和巡航导弹可携带常规和非常规弹头?常规弹头依靠弹药的爆炸产生杀伤效果,非传统弹头主要指核?生物?化学等大规模杀伤性弹头,以及旨在使设备损坏的非致命弹头?常规?生物和化学武器可装在一个弹头或多个小型炸弹中在一定高度释放?


2月,在美军联合能力技术演示验证计划支持下,美国陆军的坦克汽车研发与工程中心承担了一个为期3年的✈“僚机项目”,其目的是开发出两套可由士兵控制的自主

In [98]:
for sen, pre, true in zip(sentences, y_pre, y_true):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true)))!=[]):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: []
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('性能指标', '高精确', 81, 83), ('性能指标', '低空飞行目标', 85, 90)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40

In [125]:
df = pd.read_excel('b_test_71_0919.xlsx', index_col=0)

In [126]:
df

text  \
0    高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型...   
1    美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系...   
2    在阿尔罕格力斯克州靶场进行液体冲压发动机相关试验过程中发生的爆炸，可能与“锆石”高超声速导弹...   
3    “宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(M...   
4    俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机...   
..                                                 ...   
195  F-35项目已经完成系统开发与演示验证(SDD)阶段的最后飞行试验?该试验于4月11日在马里...   
196  美国海军水面电子战改进计划(SEWIP)显示，将在DDG✈51阿利·伯克级导弹驱逐舰上安装了...   
197  俄罗斯在保障现役反导系统延寿的同时,开展新型反导系统试验,确保其反导能力的持续发展?6月21...   
198  当地时间1月18日上午10时左右,印度进行了✈“烈火✈”-5洲际弹道导弹的发射试验?导弹从印...   
199  气动力和推进试验台（APTU）是一种下吹式风洞，可模拟提供Ma3.1-7.2的试验条件，被设...   

                                                all_70  
0    [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '...  
1    [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟...  
2    [('试验要素', '液体冲压发动机相关试验', 14, 24), ('试验要素', '“锆...  
3    [('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13), ('任务场景', '战...  
4    [('试验要素', '无人侦察支队', 8, 13), ('试验要素', '“前哨-R”无人...  
..                                                 ...  
195  [('试验要素', 'F-35项目', 1, 6), ('试验要素', '系统开发与演示验证...  
196  [('试验要素', 'DDG✈51阿利·伯克级导弹驱逐舰', 26, 42), ('试验要素...  
197  [('试验要素', '现役反导系统', 7, 12), ('试验要素', '反导系统', 9...  
198  [('试验要素', '“烈火✈”-5洲际弹道导弹', 24, 36), ('试验要素', '...  
199  [('试验要素', '气动力和推进试验台（APTU）', 1, 15), ('试验要素', ...  

[200 rows x 2 columns]

In [127]:
df['all_70'].tolist()

["[('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('性能指标', '高精确', 81, 83), ('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]",
 "[('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟踪数据', 27, 32), ('试验要素', '综合防空反导系统（IAMD）', 40, 53), ('系统组成', '战斗指挥系统（IBCS）', 55, 66), ('性能指标', '多域作战能力', 79, 84), ('性能指标', '陆军综合防空反导能力', 92, 101), ('系统组成', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '信息', 139, 140), ('试验要素', '综合防空反导系统', 144, 151), ('任务场景', '隐形战机', 162, 165)]",
 "[('试验要素', '液体冲压发动机相关试验', 14, 24), ('试验要素', '“锆石”高超声速导弹移动发射装置', 37, 52), ('试验要素', '动力装置', 114, 117)]",
 "[('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13), ('任务场景', '战区级弹道导弹', 24, 30), ('任务场景', '短程(SRBM)', 33, 40), ('任务场景', '准中程(MRBM)', 42, 50), ('任务场景', '中程弹道导弹(IRBM)', 52, 63),  ('系统组成', '雷达', 90, 91), ('试验要素', '探测和跟踪数据', 93, 99), ('任务场景', '洲际导弹导弹', 112, 117), ('任务场景', '

In [128]:
tags = [eval(line) for line in df['all_70'].tolist()[:10]]

In [129]:
tags

[[('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('性能指标', '高精确', 81, 83),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25),
  ('试验要素', '目标跟踪数据', 27, 32),
  ('试验要素', '综合防空反导系统（IAMD）', 40, 53),
  ('系统组成', '战斗指挥系统（IBCS）', 55, 66),
  ('性能指标', '多域作战能力', 79, 84),
  ('性能指标', '陆军综合防空反导能力', 92, 101),
  ('系统组成', '机载和地面战斗指挥系统', 127, 137),
  ('试验要素', '机载和地面战斗指挥系统', 127, 137),
  ('试验要素', '信息', 139, 140),
  ('试验要素', '综合防空反导系统', 144, 151),
  ('任务场景', '隐形战机', 162, 165)],
 [('试验要素', '液体冲压发动机相关试验', 14, 24),
  ('试验要素', '“锆石”高超声速导弹移动发射装置', 37, 52),
  ('试验要素', '动力装置', 114, 117)],
 [('试验要素', '“宙斯盾”弹道导弹防御系统', 1, 13),
  ('任务场景', '战区级弹道导弹', 24, 30),
  ('任务场景', '短程(SRBM)', 33, 40),
  ('任务场景', '准中程(MRBM)', 42, 50),
  ('任务场景', '中程弹道导弹(IRBM)', 52, 63),
  ('系统组成', '雷达', 90, 91),
  ('试验要素', '探测和跟踪数据', 93,

In [133]:
new_pre = []
count = 0
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff' and count <= 9:
        print('in')
        new_pre.append(tags[count])
        count += 1
    else:
        new_pre.append(true)

in
in
in
in
in
in
in
in
in
in


In [134]:
new_pre

[[('系统组成', '制导系统', 53, 56),
  ('系统组成', '特殊弹道', 38, 41),
  ('性能指标', '战术技术性能指标', 70, 77),
  ('系统组成', '固体发动机', 30, 34),
  ('系统组成', '弹头', 43, 44),
  ('系统组成', '分系统', 20, 22),
  ('性能指标', '特殊弹道', 38, 41),
  ('试验要素', '\ufeffRT-2PM2弹道导弹', 1, 12),
  ('性能指标', '战术技术性能', 70, 75),
  ('性能指标', '命中精度', 46, 49),
  ('系统组成', '快速发射', 59, 62)],
 [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27),
  ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54),
  ('系统组成', '新型激光制导系统', 66, 73),
  ('性能指标', '高精确', 81, 83),
  ('任务场景', '高精确', 81, 83),
  ('任务场景', '低空飞行目标', 85, 90),
  ('任务场景', '无人机', 94, 96),
  ('任务场景', '飞机', 98, 99),
  ('任务场景', '直升机', 101, 103),
  ('任务场景', '巡航导弹', 105, 108)],
 [('系统组成', '侧向喷嘴', 23, 26),
  ('系统组成', '侧向引擎', 6, 9),
  ('试验要素', '推力矢量', 47, 50),
  ('试验要素', '拦截点', 136, 138),
  ('系统组成', '小型引擎', 93, 96),
  ('系统组成', '推力矢量', 47, 50),
  ('系统组成', '弹体重心', 12, 15),
  ('系统组成', '侧向喷嘴', 115, 118),
  ('试验要素', '侧推力道', 59, 62),
  ('性能指标', '侧推力道', 59, 62)],
 [('性能指标', '硬目标', 131, 133),
  ('性能指标', '精度修正', 86, 89),
  ('性能指标', '精度', 106, 107),
  (

In [135]:
submit = {}
for idx, sample in enumerate(new_pre):
    sample_list = []
    for entity in sample:
        enti_dict = {
            "label_type": entity[0],
            "overlap": 0,
            "start_pos": entity[2],
            "end_pos": entity[3]
        }
        sample_list.append(enti_dict)
    submit[f"test_{idx + 1}.json"] = sample_list

with open('./en_ex42_v1.json', 'w', encoding='utf-8') as f_sub:
    # convert dict to json
    json_data = json.dumps(submit, indent=4, ensure_ascii=False)
    f_sub.write(json_data)

In [69]:
count = 0
for idx, (sen, true) in enumerate(zip(sentences, y_true)):
    if sen[0]!='\ufeff':
        if count == 100:
            print(idx)
#         print('in')
        new_pre.append(tags[count])
        count += 1

193


## HUMAN2

In [141]:
test_data_dir = Path('../data/fold0/test/')
with open(test_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen:
    sentences = [line.strip().split(' ') for line in f_sen]

In [142]:
ex1_dir = Path('../ensemble/ex42')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_true = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_true.append(sample)

In [143]:
text = []
all_70 = []
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(true, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'pre_tag':all_70
})
df.to_excel('./test_71.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。


在阿尔罕格力斯克州靶场进行液体冲压发动机相关试验过程中发生的爆炸，可能与“锆石”高超声速导弹移动发射装置有关。“锆石”导弹的研制工作正在积极开展。按照机械制造科研生产联合体需求，在红军科研所靶场对“火星”科研生产联合体所制造的动力装置进行了试验。该事件发生后几小时，第45试验场附近的德维纳湾区域禁止船只通行1个月。


“宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(MRBM)和中程弹道导弹(IRBM)?除了拦截战区级弹道导弹,“宙斯盾”弹道导弹防御系统雷达的探测和跟踪数据还可以传递给其他用于拦截洲际导弹导弹的防御系统?


俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机。“前哨-R”无人机重450kg，飞行半径达250km，时速200km/h，主要用于执行侦察任务。“牵牛星”无人机巡航速度为150-250km/h，装备雷达、光学设备、无线电设备，可执行全频谱侦察任务，可携带1吨的有效载荷。无人机不仅可以进行侦察，还可以使用高精度导弹和炸弹执行打击任务，此外无人机可以与其他打击系统联合，综合运用包括“伊斯坎德尔”导弹在内的武器。


弹道导弹和巡航导弹可携带常规和非常规弹头?常规弹头依靠弹药的爆炸产生杀伤效果,非传统弹头主要指核?生物?化学等大规模杀伤性弹头,以及旨在使设备损坏的非致命弹头?常规?生物和化学武器可装在一个弹头或多个小型炸弹中在一定高度释放?


2月,在美军联合能力技术演示验证计划支持下,美国陆军的坦克汽车研发与工程中心承担了一个为期3年的✈“僚机项目”,其目的是开发出两套可由士兵控制的自主

FileCreateError: [Errno 13] Permission denied: './test_71.xlsx'

In [144]:
df = pd.read_excel('test_71_0919_v1.xlsx', index_col=0)
tags = [eval(line) for line in df['change_tag'].tolist()[:5]]

In [146]:
new_pre = []
count = 0
for sen, true in zip(sentences, y_true):
    if sen[0]!='\ufeff' and count <= 4:
        print('in')
        new_pre.append(tags[count])
        count += 1
    else:
        new_pre.append(true)

in
in
in
in
in


In [147]:
submit = {}
for idx, sample in enumerate(new_pre):
    sample_list = []
    for entity in sample:
        enti_dict = {
            "label_type": entity[0],
            "overlap": 0,
            "start_pos": entity[2],
            "end_pos": entity[3]
        }
        sample_list.append(enti_dict)
    submit[f"test_{idx + 1}.json"] = sample_list

with open('./en_ex42_v1.json', 'w', encoding='utf-8') as f_sub:
    # convert dict to json
    json_data = json.dumps(submit, indent=4, ensure_ascii=False)
    f_sub.write(json_data)

## compare

71

In [153]:
ex1_dir = Path('../ensemble/ex42')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_pre = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_pre.append(sample)

71.2

In [152]:
ex1_dir = Path('../ensemble/ex42-4')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
y_true = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    y_true.append(sample)

71.38

In [156]:
ex1_dir = Path('../ensemble/ex54')
import json
with open(ex1_dir/'fusion_submit_extra.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_713 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_713.append(sample)

In [154]:
for sen, pre, true in zip(sentences, y_pre, y_true):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true)))!=[]):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '隐形战机', 162, 165)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('试验要素', '信息', 139, 140)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟踪数据', 27, 32), ('试验要素', '综合防空反导系统（IAMD）', 40, 53), ('试验要素', '战斗指挥系统（IBCS）', 55, 66), ('系统组成', '战斗指挥系统（IBCS）', 55, 66), ('性能指标', '多域作战能力', 79, 84), ('性能指标', '陆军综合防空反导能力', 92, 101), ('系统组成', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '综合防空反导系统', 144, 151), ('任务场景', '隐形战机', 162, 165), ('试验要素', '隐形战机', 162, 165)]
-*-

In [157]:
for sen, pre, true in zip(sentences, y_pre, test_713):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true)))!=[]):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '隐形战机', 162, 165)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: []
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟踪数据', 27, 32), ('试验要素', '综合防空反导系统（IAMD）', 40, 53), ('试验要素', '战斗指挥系统（IBCS）', 55, 66), ('系统组成', '战斗指挥系统（IBCS）', 55, 66), ('性能指标', '多域作战能力', 79, 84), ('性能指标', '陆军综合防空反导能力', 92, 101), ('系统组成', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '信息', 139, 140), ('试验要素', '综合防空反导系统', 144, 151), ('任务场景', '隐形战机', 162, 165), ('试验要素', '隐形战机', 162, 165)]
-

71.4

In [177]:
ex1_dir = Path('../ensemble/ex55')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_714 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_714.append(sample)

71.7

In [178]:
ex1_dir = Path('../ensemble/ex63')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_717 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_717.append(sample)

In [183]:
ex1_dir = Path('../ensemble/ex66')
import json
with open(ex1_dir/'fusion_submit_extra.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_718 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_718.append(sample)
text = []
all_70 = []
for sen, true in zip(sentences, test_718):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(true, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'pre_tag':all_70
})
df.to_excel('./test_718.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。


在阿尔罕格力斯克州靶场进行液体冲压发动机相关试验过程中发生的爆炸，可能与“锆石”高超声速导弹移动发射装置有关。“锆石”导弹的研制工作正在积极开展。按照机械制造科研生产联合体需求，在红军科研所靶场对“火星”科研生产联合体所制造的动力装置进行了试验。该事件发生后几小时，第45试验场附近的德维纳湾区域禁止船只通行1个月。


“宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(MRBM)和中程弹道导弹(IRBM)?除了拦截战区级弹道导弹,“宙斯盾”弹道导弹防御系统雷达的探测和跟踪数据还可以传递给其他用于拦截洲际导弹导弹的防御系统?


俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机。“前哨-R”无人机重450kg，飞行半径达250km，时速200km/h，主要用于执行侦察任务。“牵牛星”无人机巡航速度为150-250km/h，装备雷达、光学设备、无线电设备，可执行全频谱侦察任务，可携带1吨的有效载荷。无人机不仅可以进行侦察，还可以使用高精度导弹和炸弹执行打击任务，此外无人机可以与其他打击系统联合，综合运用包括“伊斯坎德尔”导弹在内的武器。


弹道导弹和巡航导弹可携带常规和非常规弹头?常规弹头依靠弹药的爆炸产生杀伤效果,非传统弹头主要指核?生物?化学等大规模杀伤性弹头,以及旨在使设备损坏的非致命弹头?常规?生物和化学武器可装在一个弹头或多个小型炸弹中在一定高度释放?


2月,在美军联合能力技术演示验证计划支持下,美国陆军的坦克汽车研发与工程中心承担了一个为期3年的✈“僚机项目”,其目的是开发出两套可由士兵控制的自主

del entity:

('任务场景', '情报', 75, 76), ('性能指标', '情报', 75, 76)

('试验要素', '短程(SRBM)', 33, 40)

('系统组成', '弹头重', 62, 64)

('试验要素', '“海军上将纳西莫夫”重型核导弹巡航舰', 130, 147)

('试验要素', '“弗吉尼亚”级“夏威夷”号核潜艇', 86, 101)(任务场景)

('试验要素', 'FA-18C/D大黄蜂战斗机', 175, 188), ('试验要素', 'FA-18E/F超级大黄蜂战斗机', 190, 205), ('试验要素', 'EA-18G咆哮者电子战机', 207, 219), ('试验要素', '狂风电子战及侦察机', 222, 230)

('性能指标', '地面固定目标', 87, 92), ('任务场景', '地面固定目标', 87, 92), ('性能指标', '移动目标', 94, 97), ('任务场景', '移动目标', 94, 97), ('任务场景', '水面目标', 99, 102), ('性能指标', '水面目标', 99, 102)

In [180]:
for sen, pre, true in zip(sentences, test_714, test_717):
    if sen[0]!='\ufeff' and list(set(pre).difference(set(true))) != []:
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

“天基红外系统”(SBIRS)的新型地面系统Block✈10增量2进入试验阶段,该系统可同时对包括“国防支援计划”(DSP)卫星?SBIRS地球同步轨道卫星?SBIRS大椭圆轨道载荷在内的全部预警卫星星座/载荷进行控制?Block✈10增量2系统将SBIRS的操作控制集成至一个主要任务控制站及一个备份控制站,大幅简化控制流程,提高运行效率?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: []
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('任务场景', '预警卫星星座/载荷', 97, 105)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '“天基红外系统”(SBIRS)', 1, 15), ('试验要素', '新型地面系统Block✈10增量2', 17, 33), ('试验要素', '“国防支援计划”(DSP)卫星', 50, 64), ('试验要素', 'SBIRS地球同步轨道卫星', 66, 78), ('试验要素', 'SBIRS大椭圆轨道载荷', 80, 91), ('试验要素', '预警卫星星座/载荷', 97, 105), ('性能指标', '操作控制', 131, 134), ('试验要素', '主要任务控制站', 140, 146), ('系统组成', '主要任务控制站', 140, 146), ('试验要素', '备份控制站', 150, 154), ('系统组成', '备份控制站', 150, 154), ('性能指标', '控制流程', 160, 163), ('性能指标', '运行效率', 167, 

In [ ]:
for sen, pre in zip(sentences, test_717):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true))) != []):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

In [179]:
for sen, pre, true in zip(sentences, test_714, test_717):
    if sen[0]!='\ufeff' and (list(set(true).difference(set(pre))) != [] or list(set(pre).difference(set(true))) != []):
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '隐形战机', 162, 165)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: []
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟踪数据', 27, 32), ('试验要素', '综合防空反导系统（IAMD）', 40, 53), ('试验要素', '战斗指挥系统（IBCS）', 55, 66), ('系统组成', '战斗指挥系统（IBCS）', 55, 66), ('性能指标', '多域作战能力', 79, 84), ('性能指标', '陆军综合防空反导能力', 92, 101), ('试验要素', '机载和地面战斗指挥系统', 127, 137), ('系统组成', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '综合防空反导系统', 144, 151), ('任务场景', '隐形战机', 162, 165), ('试验要素', '隐形战机', 162, 165)]
-*--*--*--*--*--*--*--*--*-

In [164]:
for sen, pre, true in zip(sentences, test_713, test_714):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
#         print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
#         print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
#         print('-*-'*40)
#         print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')


高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('任务场景', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-

In [176]:
text = []
all_70 = []
for sen, true in zip(sentences, test_714):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(true, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'tag':all_70
})
df.to_excel('./test_714.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。


在阿尔罕格力斯克州靶场进行液体冲压发动机相关试验过程中发生的爆炸，可能与“锆石”高超声速导弹移动发射装置有关。“锆石”导弹的研制工作正在积极开展。按照机械制造科研生产联合体需求，在红军科研所靶场对“火星”科研生产联合体所制造的动力装置进行了试验。该事件发生后几小时，第45试验场附近的德维纳湾区域禁止船只通行1个月。


“宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(MRBM)和中程弹道导弹(IRBM)?除了拦截战区级弹道导弹,“宙斯盾”弹道导弹防御系统雷达的探测和跟踪数据还可以传递给其他用于拦截洲际导弹导弹的防御系统?


俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机。“前哨-R”无人机重450kg，飞行半径达250km，时速200km/h，主要用于执行侦察任务。“牵牛星”无人机巡航速度为150-250km/h，装备雷达、光学设备、无线电设备，可执行全频谱侦察任务，可携带1吨的有效载荷。无人机不仅可以进行侦察，还可以使用高精度导弹和炸弹执行打击任务，此外无人机可以与其他打击系统联合，综合运用包括“伊斯坎德尔”导弹在内的武器。


弹道导弹和巡航导弹可携带常规和非常规弹头?常规弹头依靠弹药的爆炸产生杀伤效果,非传统弹头主要指核?生物?化学等大规模杀伤性弹头,以及旨在使设备损坏的非致命弹头?常规?生物和化学武器可装在一个弹头或多个小型炸弹中在一定高度释放?


2月,在美军联合能力技术演示验证计划支持下,美国陆军的坦克汽车研发与工程中心承担了一个为期3年的✈“僚机项目”,其目的是开发出两套可由士兵控制的自主

## new

In [184]:
ex1_dir = Path('../ensemble/ex63')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_717 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_717.append(sample)

In [185]:
ex1_dir = Path('../ensemble')
import json
with open(ex1_dir/'extra.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
extra = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    extra.append(sample)

In [186]:
for sen, pre, true in zip(sentences, extra, test_717):
    if sen[0]!='\ufeff' and list(set(pre).difference(set(true))) != []:
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
        print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
        print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
        print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: []
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
low: [('试验要素', '信息', 139, 140)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', 'F-35闪电Ⅱ战斗机', 16, 25), ('试验要素', '目标跟踪数据', 27, 32), ('试验要素', '综合防空反导系统（IAMD）', 40, 53), ('试验要素', '战斗指挥系统（IBCS）', 55, 66), ('系统组成', '战斗指挥系统（IBCS）', 55, 66), ('性能指标', '多域作战能力', 79, 84), ('性能指标', '陆军综合防空反导能力', 92, 101), ('试验要素', '机载和地面战斗指挥系统', 127, 137), ('系统组成', '机载和地面战斗指挥系统', 127, 137), ('试验要素', '综合防空反导系统', 144, 151), ('任务场景', '隐形战机', 162, 165), ('试验要素', '隐形战机', 162, 165)]
-*--*--*--*--*--*--*--*--*--*

## HUMAN2

In [187]:
test_data_dir = Path('../data/fold0/test/')
with open(test_data_dir/'sentences.txt', 'r', encoding='utf-8') as f_sen:
    sentences = [line.strip().split(' ') for line in f_sen]

In [191]:
ex1_dir = Path('../ensemble/ex42')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_710 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_710.append(sample)

In [192]:
text = []
all_70 = []
for sen, true in zip(sentences, test_718):
    if sen[0]!='\ufeff':
        print("".join(sen))
        print('\n')
        text.append("".join(sen))
        all_70.append(sorted(true, key=lambda p: p[2]))
df = pd.DataFrame({
    'text':text,
    'pre_tag':all_70
})
df.to_excel('./test_710.xlsx')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-35战斗机已经实现了首次通过机载和地面战斗指挥系统将信息发送给综合防空反导系统，这一系统的结合成为隐形战机能力提升的重要里程碑。


在阿尔罕格力斯克州靶场进行液体冲压发动机相关试验过程中发生的爆炸，可能与“锆石”高超声速导弹移动发射装置有关。“锆石”导弹的研制工作正在积极开展。按照机械制造科研生产联合体需求，在红军科研所靶场对“火星”科研生产联合体所制造的动力装置进行了试验。该事件发生后几小时，第45试验场附近的德维纳湾区域禁止船只通行1个月。


“宙斯盾”弹道导弹防御系统最初设计主要用于拦截战区级弹道导弹,即短程(SRBM)?准中程(MRBM)和中程弹道导弹(IRBM)?除了拦截战区级弹道导弹,“宙斯盾”弹道导弹防御系统雷达的探测和跟踪数据还可以传递给其他用于拦截洲际导弹导弹的防御系统?


俄军将组建首支无人侦察支队，配备最新“前哨-R”无人机，未来将装备更加先进的“牵牛星”无人机。“前哨-R”无人机重450kg，飞行半径达250km，时速200km/h，主要用于执行侦察任务。“牵牛星”无人机巡航速度为150-250km/h，装备雷达、光学设备、无线电设备，可执行全频谱侦察任务，可携带1吨的有效载荷。无人机不仅可以进行侦察，还可以使用高精度导弹和炸弹执行打击任务，此外无人机可以与其他打击系统联合，综合运用包括“伊斯坎德尔”导弹在内的武器。


弹道导弹和巡航导弹可携带常规和非常规弹头?常规弹头依靠弹药的爆炸产生杀伤效果,非传统弹头主要指核?生物?化学等大规模杀伤性弹头,以及旨在使设备损坏的非致命弹头?常规?生物和化学武器可装在一个弹头或多个小型炸弹中在一定高度释放?


2月,在美军联合能力技术演示验证计划支持下,美国陆军的坦克汽车研发与工程中心承担了一个为期3年的✈“僚机项目”,其目的是开发出两套可由士兵控制的自主

In [197]:
ex1_dir = Path('../ensemble')
import json
with open(ex1_dir/'fusion_submit.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_717 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_717.append(sample)

In [202]:
ex1_dir = Path('../ensemble/ex68')
import json
with open(ex1_dir/'ex68.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_718 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_718.append(sample)

In [204]:
for sen, true in zip(sentences, test_718):
    if sen[0]!='\ufeff' and list(set(pre).difference(set(true))) != []:
        print("".join(sen))
        print('-*-'*40)
        # 真实标签里有而预测结果里没有的（影响Recall）
#         print('high:',sorted(list(set(true).difference(set(pre))), key=lambda p: p[2]))
        print('-*-'*40)
        # 预测结果里有而真实标签里没有的（影响Precision）
#         print('low:',sorted(list(set(pre).difference(set(true))), key=lambda p: p[2]))
        print('-*-'*40)
        print('high:',sorted(true, key=lambda p: p[2]))
        print('-*-'*40)
#         print('low:',sorted(pre, key=lambda p: p[2]))
        print('\n')

高精确系统有限公司已完成了✈“杜香✈”新型防空导弹系统试验,即将进入列装阶段?“杜香✈”新型近程防空导弹系统已研发10余年,具备最新型激光制导系统,主要用于打击高精确?低空飞行目标,包括无人机?飞机?直升机和巡航导弹等?
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-
high: [('试验要素', '“杜香✈”新型防空导弹系统', 15, 27), ('试验要素', '“杜香✈”新型近程防空导弹系统', 40, 54), ('系统组成', '新型激光制导系统', 66, 73), ('任务场景', '高精确', 81, 83), ('性能指标', '高精确', 81, 83), ('任务场景', '低空飞行目标', 85, 90), ('任务场景', '无人机', 94, 96), ('任务场景', '飞机', 98, 99), ('任务场景', '直升机', 101, 103), ('任务场景', '巡航导弹', 105, 108)]
-*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*--*-


美国空军在最近进行的试验中，将F-35闪电Ⅱ战斗机的目标跟踪数据，与美国陆军的综合防空反导系统（IAMD）的战斗指挥系统（IBCS）相结合，使F-35战机的多域作战能力进一步提升，而陆军综合防空反导能力也有所提升。目前，F-

In [256]:
import re
for sen in sentences:
    if sen[0]!='\ufeff':
        if re.findall(r'用于打击(.+)、(.+)及(.+)，', "".join(sen)) != []:
            print("".join(sen))
            print(re.findall(r'用于打击(.+)、(.+)及(.+)，', "".join(sen)))

诺格公司向美国海军交付第1000枚先进反辐射导弹（AARGM）。先进反辐射导弹是美国海军与意大利空军联合研制的超声速空射反辐射导弹，采用双模制导，可全天候作战，主要用于打击地面固定目标、移动目标及水面目标，如装甲车、薄皮车辆、海上巡逻艇、城市建筑物和野外防御工事等。目前已部署到美国海军、美国海军陆战队、意大利空军和澳大利亚皇家空军。该导弹已集成到FA-18C/D大黄蜂战斗机、FA-18E/F超级大黄蜂战斗机、EA-18G咆哮者电子战机以及狂风电子战及侦察机等作战平台上。
[('地面固定目标', '移动目标', '水面目标')]
日本正在开发两种先进的反舰弹头，“海上克星”串联战斗部和多爆炸成形弹丸（MEFP）战斗部，以适配其正在发展的两种高超声速武器。用于打击对手部署在岛屿及周边的军舰和车辆。“海上克星”战斗部是专门针对敌方水面舰艇研发的，由一枚携带穿甲高爆弹壳、一枚鼻引信的主弹头以及一枚使用聚能装药的前体弹头组成。日本曾经公布过这种战斗部打击水面舰艇的示意图，用来打击敌方航母甲板等大型舰艇目标。而多爆炸成形弹丸（MEFP）战斗部则用于对付水面舰艇和固定或移动地面目标，可释放几十个能够打击数个目标的超高速金属碎片。
[('对手部署在岛屿及周边的军舰和车辆。“海上克星”战斗部是专门针对敌方水面舰艇研发的，由一枚携带穿甲高爆弹壳', '一枚鼻引信的主弹头以', '一枚使用聚能装药的前体弹头组成。日本曾经公布过这种战斗部打击水面舰艇的示意图，用来打击敌方航母甲板等大型舰艇目标。而多爆炸成形弹丸（MEFP）战斗部则用于对付水面舰艇和固定或移动地面目标')]


In [208]:
str1 = "诺格公司向美国海军交付第1000枚先进反辐射导弹（AARGM）。先进反辐射导弹是美国海军与意大利空军联合研制的超声速空射反辐射导弹，采用双模制导，可全天候作战，主要用于打击地面固定目标、移动目标及水面目标，如装甲车、薄皮车辆、海上巡逻艇、城市建筑物和野外防御工事等。目前已部署到美国海军、美国海军陆战队、意大利空军和澳大利亚皇家空军。该导弹已集成到FA-18C/D大黄蜂战斗机、FA-18E/F超级大黄蜂战斗机、EA-18G咆哮者电子战机以及狂风电子战及侦察机等作战平台上。"

In [223]:
re.findall(r'打击(.+)、(.+)及(.+)，', str1)

[('地面固定目标', '移动目标', '水面目标')]

In [227]:
from itertools import chain
all_pre_ens = list(chain(*y_true))

In [228]:
from itertools import groupby

In [233]:
import pandas as pd

In [235]:
df = pd.DataFrame(
    {
        "type": [en[0] for en in all_pre_ens],
        "content": [en[1] for en in all_pre_ens]
    }
)

In [242]:
per = df.iloc[df.groupby('type').groups['性能指标']].content.tolist()

In [245]:
for p in per:
    if '目标' in p:
        print(p)

硬目标
超音速目标
空中目标
多目标交战能力
水下目标
目标检测和跟踪过程
空中目标
空中目标
威胁目标
真目标
机动目标
目标数据
目标
标定目标信息
硬目标
低空目标
高机动目标
地面固定目标
移动目标
水面目标
目标特征
目标特征匹配
可攻击地面目标集
低空小型无人机目标
气动力目标
低空目标
高机动目标
近距离移动目标
高机动目标
对抗措施目标
近岸目标打击能力
来袭目标
目标
特定目标
多目标能力
超视距目标信息
目标轨道
弹道导弹目标
空气动力目标
目标弹头
隐形目标
硬目标
海上移动目标
目标选择性能
敌方雷达和导弹目标
固定或移动地面目标
气动目标
目标类型
气动目标
弹道目标
高速目标
高威胁目标
跟踪目标数量
弹道目标
毁伤目标
弹道目标
目标探测距离
空气动力目标
空气动力目标
同时跟踪目标数量
空中目标
水面目标
目标地图匹配
静止或移动目标
小反射截面高速弹道目标
目标雷达
密集多目标空袭
目标识别


In [ ]:
def rule_6(entities, text):
#     pat1 = re.findall(r'用于打击(.+)、(.+)及(.+)，', text)
    pat2 = re.findall(r'已集成到(.+)、(.+)、(.+)以及(.+)等', text)
    result = []
    if pat2:
        # 全部小于等于10
        for en in entities:
                for p in pat2:
#                     print(p)
                    if en[1] == p:
                        result.append(('任务场景', en[1], en[2], en[3]))
                        break
#                         print(('任务场景', en[1], en[2], en[3]))
#                         print(idx)
                else:
                    result.append(en)
    else:
        result = entities
    return result

In [322]:
def rule_6(entities, text):
    pat1 = re.findall(r'用于打击(.+)、(.+)及(.+)，', text)
    pat2 = re.findall(r'已集成到(.+)、(.+)、(.+)以及(.+)等', text)
    result = []
    if pat1:
        # 全部小于等于10
        if not any([False if len(en_con) < 10 else True for en_con in pat1[0]]):
            for en in entities:
                for p in pat1[0]:
#                     print(en)
#                     print(p)
                    if en[1] == p:
                        result.append(('任务场景', en[1], en[2], en[3]))
                        break
#                         print(('任务场景', en[1], en[2], en[3]))
#                         print(idx)
                else:
                    result.append(en)
    else:
        result = entities
    return result

In [307]:
ex1_dir = Path('../ensemble/ex68')
import json
with open(ex1_dir/'ex68.json', 'r', encoding='utf-8') as f:
    pre = json.load(f)
test_718 = []
for idx in range(1, len(pre)+1):
    text = ''.join(sentences[idx-1])
    entities = pre[f'test_{idx}.json']
    sample = []
    for entity in entities:
        entity_con = text[entity['start_pos']-1:entity['end_pos']]
        sample.append((entity['label_type'], entity_con, entity['start_pos'], entity['end_pos']))
    test_718.append(sample)

In [312]:
for idx, entities in enumerate(test_718):
    result = rule_6(entities, "".join(sentences[idx]))

('任务场景', '地面固定目标', 87, 92)
100
('任务场景', '地面固定目标', 87, 92)
100
('任务场景', '移动目标', 94, 97)
100
('任务场景', '移动目标', 94, 97)
100
('任务场景', '水面目标', 99, 102)
100
('任务场景', '水面目标', 99, 102)
100


In [313]:
test_718[100]

[('试验要素', '先进反辐射导弹（AARGM）', 18, 31),
 ('任务场景', '超声速空射反辐射导弹', 56, 65),
 ('试验要素', '超声速空射反辐射导弹', 56, 65),
 ('系统组成', '双模制导', 69, 72),
 ('性能指标', '双模制导', 69, 72),
 ('性能指标', '全天候', 75, 77),
 ('性能指标', '地面固定目标', 87, 92),
 ('任务场景', '地面固定目标', 87, 92),
 ('任务场景', '移动目标', 94, 97),
 ('性能指标', '移动目标', 94, 97),
 ('任务场景', '水面目标', 99, 102),
 ('性能指标', '水面目标', 99, 102),
 ('任务场景', '装甲车', 105, 107),
 ('任务场景', '薄皮车辆', 109, 112),
 ('任务场景', '海上巡逻艇', 114, 118),
 ('任务场景', '城市建筑物', 120, 124),
 ('任务场景', '野外防御工事', 126, 131),
 ('任务场景', '美国海军', 140, 143),
 ('任务场景', '美国海军陆战队', 145, 151),
 ('任务场景', '意大利空军', 153, 157),
 ('任务场景', '澳大利亚皇家空军', 159, 166),
 ('试验要素', 'FA-18C/D大黄蜂战斗机', 175, 188),
 ('试验要素', 'FA-18E/F超级大黄蜂战斗机', 190, 205),
 ('试验要素', 'EA-18G咆哮者电子战机', 207, 219),
 ('试验要素', '狂风电子战及侦察机', 222, 230),
 ('试验要素', '作战平台', 232, 235),
 ('任务场景', '作战平台', 232, 235)]

In [327]:
text = "".join(sentences[100])

In [331]:
for sen in sentences:
    text = "".join(sen)
    if re.findall(r'已集成到(.+)、(.+)、(.+)以及(.+)等', text):
        print(re.findall(r'已集成到(.+)、(.+)、(.+)以及(.+)等', text))

[('FA-18C/D大黄蜂战斗机', 'FA-18E/F超级大黄蜂战斗机', 'EA-18G咆哮者电子战机', '狂风电子战及侦察机')]


In [323]:
rule_6(test_718[100], "".join(sentences[100]))

[('试验要素', '先进反辐射导弹（AARGM）', 18, 31),
 ('任务场景', '超声速空射反辐射导弹', 56, 65),
 ('试验要素', '超声速空射反辐射导弹', 56, 65),
 ('系统组成', '双模制导', 69, 72),
 ('性能指标', '双模制导', 69, 72),
 ('性能指标', '全天候', 75, 77),
 ('任务场景', '地面固定目标', 87, 92),
 ('任务场景', '地面固定目标', 87, 92),
 ('任务场景', '移动目标', 94, 97),
 ('任务场景', '移动目标', 94, 97),
 ('任务场景', '水面目标', 99, 102),
 ('任务场景', '水面目标', 99, 102),
 ('任务场景', '装甲车', 105, 107),
 ('任务场景', '薄皮车辆', 109, 112),
 ('任务场景', '海上巡逻艇', 114, 118),
 ('任务场景', '城市建筑物', 120, 124),
 ('任务场景', '野外防御工事', 126, 131),
 ('任务场景', '美国海军', 140, 143),
 ('任务场景', '美国海军陆战队', 145, 151),
 ('任务场景', '意大利空军', 153, 157),
 ('任务场景', '澳大利亚皇家空军', 159, 166),
 ('试验要素', 'FA-18C/D大黄蜂战斗机', 175, 188),
 ('试验要素', 'FA-18E/F超级大黄蜂战斗机', 190, 205),
 ('试验要素', 'EA-18G咆哮者电子战机', 207, 219),
 ('试验要素', '狂风电子战及侦察机', 222, 230),
 ('试验要素', '作战平台', 232, 235),
 ('任务场景', '作战平台', 232, 235)]